In [218]:
# Import all the necessary modules
import os
import sys
import os, sys
# from .../research/notebooks -> go up two levels to repo root
repo_root = os.path.abspath(os.path.join(os.getcwd(), "..", ".."))
if repo_root not in sys.path:
    sys.path.insert(0, repo_root)

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import matplotlib.ticker as mtick
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn import linear_model
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score 
import pandas_datareader as pdr
import math
import datetime
from datetime import datetime, timezone
import itertools
import ast
import yfinance as yf
import seaborn as sn
from IPython.display import display, HTML
from strategy_signal.trend_following_signal import (
    apply_jupyter_fullscreen_css, get_trend_donchian_signal_for_portfolio_with_rolling_r_sqr_vol_of_vol
)
from portfolio.strategy_performance import (calculate_sharpe_ratio, calculate_calmar_ratio, calculate_CAGR, calculate_risk_and_performance_metrics,
                                          calculate_compounded_cumulative_returns, estimate_fee_per_trade, rolling_sharpe_ratio)
from utils import coinbase_utils as cn
from portfolio import strategy_performance as perf
from sizing import position_sizing_binary_utils as size_bin
from sizing import position_sizing_continuous_utils as size_cont
from strategy_signal import trend_following_signal as tf
%matplotlib inline

In [282]:
import importlib
importlib.reload(cn)
importlib.reload(perf)
importlib.reload(tf)
importlib.reload(size_bin)
importlib.reload(size_cont)

<module 'sizing.position_sizing_continuous_utils' from '/Users/adheerchauhan/Documents/git/trend_following/sizing/position_sizing_continuous_utils.py'>

In [8]:
import warnings
warnings.filterwarnings('ignore')
pd.set_option('Display.max_rows', None)
pd.set_option('Display.max_columns',None)
apply_jupyter_fullscreen_css()

In [24]:
from pathlib import Path
import yaml

def load_prod_strategy_config(strategy_version='v0.1.0'):

    nb_cwd = Path.cwd()  # git/trend_following/research/notebooks
    config_path = (
        nb_cwd.parents[1]                    # -> git/trend_following
        / "live_strategy"
        / f"trend_following_strategy_{strategy_version}-live"
        / "config"
        / f"trend_strategy_config_{strategy_version}.yaml"
    )
    
    print(config_path)            # sanity check
    print(config_path.exists())   # should be True
    
    with open(config_path, "r") as f:
        cfg = yaml.safe_load(f)

    return cfg

In [90]:
def get_live_portfolio_equity_and_cash(client, portfolio_name='Default'):

    ## Get Portfolio UUID and Positions
    portfolio_uuid = cn.get_portfolio_uuid(client, portfolio_name)
    df_portfolio_positions = cn.get_portfolio_breakdown(client, portfolio_uuid)

    ## Get Portfolio Value and Available Cash
    cash_cond = (df_portfolio_positions.is_cash == True)
    portfolio_equity = float(df_portfolio_positions[~cash_cond]['total_balance_fiat'].sum())
    available_cash = float(df_portfolio_positions[cash_cond]['available_to_trade_fiat'].sum())

    return portfolio_equity, available_cash

In [92]:
def get_price_map(client, ticker_list):
    result_dict = {}
    for ticker in ticker_list:
        ## Get Best Bid and Offer Data
        book = client.get_product_book(ticker, limit=1)['pricebook']
    
        ## Build Price Dictionary
        price_dict = {'best_bid_price': float(book['bids'][0]['price']),
                      'best_bid_size': float(book['bids'][0]['size']),
                      'best_ask_price': float(book['asks'][0]['price']),
                      'best_ask_size': float(book['asks'][0]['size']),
                      'best_mid_price': (float(book['bids'][0]['price']) + float(book['asks'][0]['price'])) / 2}
    
        result_dict[ticker] = price_dict

    return result_dict

In [94]:
def get_current_positions_from_portfolio(client, ticker_list, portfolio_name='Default'):

    df_portfolio = cn.get_portfolio_breakdown(client, portfolio_uuid=cn.get_portfolio_uuid(client, portfolio_name))
    price_map = get_price_map(client, ticker_list)

    ticker_result = {}
    for ticker in ticker_list:
        ticker_cond = (df_portfolio['asset'] == ticker[:-4])
        if df_portfolio[ticker_cond].shape[0] > 0:
            ticker_qty = float(df_portfolio[ticker_cond]['total_balance_crypto'])
        else:
            ticker_qty = 0
        ticker_mid_price = float(price_map[ticker]['best_mid_price'])
        ticker_result[ticker] = {'ticker_qty': ticker_qty,
                                 'ticker_mid_price': ticker_mid_price,
                                 'ticker_current_notional': ticker_qty * ticker_mid_price}

    return ticker_result

In [984]:
def get_strategy_trend_signal(cfg):

    end_date = datetime.now(timezone.utc).date()
    start_date = end_date - pd.Timedelta(days=cfg['run']['warmup_days'])

    # Build kwargs directly from cfg sections
    sig_kwargs = {
        # Dates
        "start_date": start_date,
        "end_date": end_date,

        # Universe
        "ticker_list": cfg["universe"]["tickers"],

        # Moving Average Signal
        "fast_mavg": cfg["signals"]["moving_average"]["fast_mavg"],
        "slow_mavg": cfg["signals"]["moving_average"]["slow_mavg"],
        "mavg_stepsize": cfg["signals"]["moving_average"]["mavg_stepsize"],
        "mavg_z_score_window": cfg["signals"]["moving_average"]["mavg_z_score_window"],

        # Donchain Channel Signal
        "entry_rolling_donchian_window": cfg["signals"]["donchian"]["entry_rolling_donchian_window"],
        "exit_rolling_donchian_window": cfg["signals"]["donchian"]["exit_rolling_donchian_window"],
        "use_donchian_exit_gate": cfg["signals"]["donchian"]["use_donchian_exit_gate"],

        # Signal Weights
        "ma_crossover_signal_weight": cfg["signals"]["weighting"]["ma_crossover_signal_weight"],
        "donchian_signal_weight": cfg["signals"]["weighting"]["donchian_signal_weight"],
        "weighted_signal_ewm_window": cfg["signals"]["weighting"]["weighted_signal_ewm_window"],
        "rolling_r2_window": cfg["signals"]["filters"]["rolling_r2"]["rolling_r2_window"],

        # Rolling R Squared Filter
        "lower_r_sqr_limit": cfg["signals"]["filters"]["rolling_r2"]["lower_r_sqr_limit"],
        "upper_r_sqr_limit": cfg["signals"]["filters"]["rolling_r2"]["upper_r_sqr_limit"],
        "r2_smooth_window": cfg["signals"]["filters"]["rolling_r2"]["r2_smooth_window"],
        "r2_confirm_days": cfg["signals"]["filters"]["rolling_r2"]["r2_confirm_days"],

        # Vol of Vol Filter
        "log_std_window": cfg["signals"]["filters"]["vol_of_vol"]["log_std_window"],
        "coef_of_variation_window": cfg["signals"]["filters"]["vol_of_vol"]["coef_of_variation_window"],
        "vol_of_vol_z_score_window": cfg["signals"]["filters"]["vol_of_vol"]["vol_of_vol_z_score_window"],
        "vol_of_vol_p_min": cfg["signals"]["filters"]["vol_of_vol"]["vol_of_vol_p_min"],
        "r2_strong_threshold": cfg["signals"]["filters"]["rolling_r2"]["r2_strong_threshold"],

        # Signal & Data Parameters
        "use_activation": cfg["signals"]["activation"]["use_activation"],
        "tanh_activation_constant_dict": cfg["signals"]["activation"]["tanh_activation_constant_dict"],
        "moving_avg_type": cfg["data"]["moving_avg_type"],
        "long_only": cfg["run"]["long_only"],
        "price_or_returns_calc": cfg["data"]["price_or_returns_calc"],
        "use_coinbase_data": cfg["data"]["use_coinbase_data"],
        "use_saved_files": False,
        "saved_file_end_date": cfg["data"]["saved_file_end_date"]
    }
    
    df_trend = get_trend_donchian_signal_for_portfolio_with_rolling_r_sqr_vol_of_vol(**sig_kwargs)

    print('Generating Volatility Adjusted Trend Signal!!')
    ## Get Volatility Adjusted Trend Signal
    df_signal = size_cont.get_volatility_adjusted_trend_signal_continuous(df_trend, ticker_list=cfg['universe']['tickers'],
                                                                          volatility_window=cfg['risk_and_sizing']['volatility_window'],
                                                                          annual_trading_days=cfg['run']['annual_trading_days'])

    print('Getting Average True Range for Stop Loss Calculation!!')
    ## Get Average True Range for Stop Loss Calculation
    atr_kwargs = {
        # dates
        "start_date": start_date,
        "end_date": end_date,
        
        # run / universe / data
        "ticker_list": cfg["universe"]["tickers"],
    
        # risk and sizing
        "rolling_atr_window": cfg['risk_and_sizing']['rolling_atr_window'],
    
        # data
        "price_or_returns_calc": cfg['data']['price_or_returns_calc'],
        "use_coinbase_data": cfg['data']['use_coinbase_data'],
        "use_saved_files": False,
        "saved_file_end_date": cfg['data']['saved_file_end_date']
    }
    df_atr = size_cont.get_average_true_range_portfolio(**atr_kwargs)
    df_signal = pd.merge(df_signal, df_atr, left_index=True, right_index=True, how='left')

    return df_signal

In [900]:
cfg = load_prod_strategy_config()
end_date = datetime.now().date()
start_date = end_date - pd.Timedelta(days=cfg['run']['warmup_days'])

/Users/adheerchauhan/Documents/git/trend_following/live_strategy/trend_following_strategy_v0.1.0-live/config/trend_strategy_config_v0.1.0.yaml
True


In [902]:
df_signal = get_strategy_trend_signal(cfg)

Generating Volatility Adjusted Trend Signal!!
Getting Average True Range for Stop Loss Calculation!!


In [908]:
print(start_date, end_date)

2024-11-21 2025-09-17


In [904]:
df_close = cn.save_historical_crypto_prices_from_coinbase(ticker='BTC-USD', user_start_date=True, start_date=start_date,
                                                          end_date=end_date, save_to_file=False)

In [920]:
df_close = cn.save_historical_crypto_prices_from_coinbase(ticker='BTC-USD', user_start_date=True, start_date=pd.Timestamp('2024-11-21').date(),
                                                          end_date=pd.Timestamp('2025-09-18').date(), save_to_file=False)

In [922]:
df_close.tail()

low       high       open      close       volume
date                                                               
2025-09-14  115166.00  116226.61  115968.33  115314.13  1967.886838
2025-09-15  114395.84  116802.00  115314.12  115381.08  6142.678595
2025-09-16  114750.00  117000.00  115381.07  116832.56  6012.583134
2025-09-17  114724.57  117327.24  116832.56  116484.40  7151.300338
2025-09-18  116125.08  116913.22  116484.40  116787.33   396.328570

In [914]:
df_close.tail()

low       high       open      close       volume
date                                                               
2025-09-14  115166.00  116226.61  115968.33  115314.13  1967.886838
2025-09-15  114395.84  116802.00  115314.12  115381.08  6142.678595
2025-09-16  114750.00  117000.00  115381.07  116832.56  6012.583134
2025-09-17  114724.57  117327.24  116832.56  116484.40  7151.300338
2025-09-18  116125.08  116913.22  116484.40  116759.37   394.698169

In [924]:
## Get Live Portfolio Equity
portfolio_name = cfg['portfolio']['name']
cn_client = cn.get_coinbase_rest_api_client(portfolio_name)
portfolio_equity, available_cash = get_live_portfolio_equity_and_cash(client=cn_client, portfolio_name=portfolio_name)

## Get Portfolio Breakdown
cn_client = cn.get_coinbase_rest_api_client(portfolio_name=portfolio_name)
df_portfolio_breakdown = cn.get_portfolio_breakdown(cn_client, portfolio_uuid=cn.get_portfolio_uuid(cn_client, portfolio_name=portfolio_name))

## Get Current Positions using Mid-Price
## TODO: CHECK TO SEE IF THE MID-PRICE BEING CAPTURED IS ACCURATE FROM COINBASE
cn_client = cn.get_coinbase_rest_api_client(portfolio_name=portfolio_name)
current_positions = get_current_positions_from_portfolio(cn_client, ticker_list=cfg['universe']['tickers'], portfolio_name=portfolio_name)

In [926]:
current_positions

{'BTC-USD': {'ticker_qty': 0,
  'ticker_mid_price': 116767.515,
  'ticker_current_notional': 0.0},
 'ETH-USD': {'ticker_qty': 0,
  'ticker_mid_price': 4628.415,
  'ticker_current_notional': 0.0},
 'SOL-USD': {'ticker_qty': 0,
  'ticker_mid_price': 246.79500000000002,
  'ticker_current_notional': 0.0},
 'ADA-USD': {'ticker_qty': 0,
  'ticker_mid_price': 0.91615,
  'ticker_current_notional': 0.0},
 'AVAX-USD': {'ticker_qty': 0,
  'ticker_mid_price': 32.575,
  'ticker_current_notional': 0.0}}

In [928]:
print(portfolio_equity)
print(available_cash)

0.0
1000.0


In [930]:
asset_list = cfg['universe']['tickers']
asset_list = [i[:-4] for i in asset_list]
df_portfolio_breakdown#[df_portfolio_breakdown.asset.isin(asset_list)]

asset                          account_uuid asset_uuid  total_balance_fiat  \
0   USD  7ebde10b-30e9-5200-aea2-000837e4dcc5                           1000   

   available_to_trade_fiat  total_balance_crypto  allocation cost_basis_value  \
0                     1000                  1000           1             1000   

  cost_basis_currency  is_cash average_entry_price_value  \
0                 USD     True                         1   

  average_entry_price_currency  available_to_trade_crypto  unrealized_pnl  \
0                          USD                       1000               0   

   available_to_transfer_fiat  available_to_transfer_crpyto  
0                        1000                          1000

In [932]:
signal_cols = [f'{ticker}_final_signal' for ticker in cfg['universe']['tickers']]
vol_adj_signal_cols = [f'{ticker}_vol_adjusted_trend_signal' for ticker in cfg['universe']['tickers']]
returns_cols = [f'{ticker}_t_1_close_pct_returns' for ticker in cfg['universe']['tickers']]

In [934]:
df_signal[returns_cols].tail()

BTC-USD_t_1_close_pct_returns  ETH-USD_t_1_close_pct_returns  \
date                                                                       
2025-09-14                      -0.001186                      -0.009685   
2025-09-15                      -0.005641                      -0.013508   
2025-09-16                       0.000581                      -0.017666   
2025-09-17                       0.012580                      -0.004831   
2025-09-18                      -0.002980                       0.019870   

            SOL-USD_t_1_close_pct_returns  ADA-USD_t_1_close_pct_returns  \
date                                                                       
2025-09-14                       0.000578                       0.013296   
2025-09-15                      -0.010887                      -0.044526   
2025-09-16                      -0.022972                      -0.028028   
2025-09-17                       0.011351                       0.019687   
2025-09-18                       0.033332                       0.037706   

            AVAX-USD_t_1_close_pct_returns  
date                                        
2025-09-14                        0.037918  
2025-09-15                       -0.021255  
2025-09-16                        0.011537  
2025-09-17                        0.009057  
2025-09-18                        0.057846

In [936]:
df_signal[signal_cols + vol_adj_signal_cols].tail()

BTC-USD_final_signal  ETH-USD_final_signal  SOL-USD_final_signal  \
date                                                                           
2025-09-14                   0.0              0.317216              0.363895   
2025-09-15                   0.0              0.315698              0.370252   
2025-09-16                   0.0              0.309804              0.372970   
2025-09-17                   0.0              0.302844              0.378887   
2025-09-18                   0.0              0.300179              0.391777   

            ADA-USD_final_signal  AVAX-USD_final_signal  \
date                                                      
2025-09-14              0.054826               0.061138   
2025-09-15              0.090685               0.130784   
2025-09-16              0.135594               0.193028   
2025-09-17              0.172116               0.212830   
2025-09-18              0.182799               0.238547   

            BTC-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-14                                0.0   
2025-09-15                                0.0   
2025-09-16                                0.0   
2025-09-17                                0.0   
2025-09-18                                0.0   

            ETH-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-14                           0.406594   
2025-09-15                           0.406409   
2025-09-16                           0.397395   
2025-09-17                           0.388730   
2025-09-18                           0.389770   

            SOL-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-14                           0.446921   
2025-09-15                           0.461542   
2025-09-16                           0.461098   
2025-09-17                           0.468362   
2025-09-18                           0.494440   

            ADA-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-14                           0.077578   
2025-09-15                           0.125967   
2025-09-16                           0.188077   
2025-09-17                           0.243301   
2025-09-18                           0.258244   

            AVAX-USD_vol_adjusted_trend_signal  
date                                            
2025-09-14                            0.068098  
2025-09-15                            0.144681  
2025-09-16                            0.213852  
2025-09-17                            0.236856  
2025-09-18                            0.269099

In [938]:
returns_cols = [f'{ticker}_t_1_close_pct_returns' for ticker in cfg['universe']['tickers']]
cov_matrix = df_signal[returns_cols].rolling(cfg['risk_and_sizing']['rolling_cov_window']).cov(pairwise=True).dropna()

In [940]:
cov_matrix.loc[end_date].loc[returns_cols, returns_cols]

BTC-USD_t_1_close_pct_returns  \
BTC-USD_t_1_close_pct_returns                        0.000160   
ETH-USD_t_1_close_pct_returns                        0.000133   
SOL-USD_t_1_close_pct_returns                        0.000280   
ADA-USD_t_1_close_pct_returns                        0.000217   
AVAX-USD_t_1_close_pct_returns                       0.000342   

                                ETH-USD_t_1_close_pct_returns  \
BTC-USD_t_1_close_pct_returns                        0.000133   
ETH-USD_t_1_close_pct_returns                        0.000433   
SOL-USD_t_1_close_pct_returns                        0.000447   
ADA-USD_t_1_close_pct_returns                        0.000308   
AVAX-USD_t_1_close_pct_returns                       0.000256   

                                SOL-USD_t_1_close_pct_returns  \
BTC-USD_t_1_close_pct_returns                        0.000280   
ETH-USD_t_1_close_pct_returns                        0.000447   
SOL-USD_t_1_close_pct_returns                        0.000968   
ADA-USD_t_1_close_pct_returns                        0.000646   
AVAX-USD_t_1_close_pct_returns                       0.000668   

                                ADA-USD_t_1_close_pct_returns  \
BTC-USD_t_1_close_pct_returns                        0.000217   
ETH-USD_t_1_close_pct_returns                        0.000308   
SOL-USD_t_1_close_pct_returns                        0.000646   
ADA-USD_t_1_close_pct_returns                        0.000618   
AVAX-USD_t_1_close_pct_returns                       0.000592   

                                AVAX-USD_t_1_close_pct_returns  
BTC-USD_t_1_close_pct_returns                         0.000342  
ETH-USD_t_1_close_pct_returns                         0.000256  
SOL-USD_t_1_close_pct_returns                         0.000668  
ADA-USD_t_1_close_pct_returns                         0.000592  
AVAX-USD_t_1_close_pct_returns                        0.001533

In [1022]:
def get_target_notional_by_ticker(df, date, ticker_list, initial_capital, rolling_cov_window,
                                  rolling_atr_window, atr_multiplier, cash_buffer_percentage,
                                  annualized_target_volatility, transaction_cost_est=0.001,
                                  passive_trade_rate=0.05, notional_threshold_pct=0.02,
                                  min_trade_notional_abs=10, cooldown_counter_threshold=3,
                                  annual_trading_days=365, use_specific_start_date=False,
                                  signal_start_date=None, portfolio_name='Default'):
    ## Create Coinbase Client & Portfolio UUID
    client = cn.get_coinbase_rest_api_client(portfolio_name=portfolio_name)
    portfolio_uuid = cn.get_portfolio_uuid(client, portfolio_name=portfolio_name)

    ## Get Live Portfolio Equity
    portfolio_equity, available_cash = get_live_portfolio_equity_and_cash(client=client, portfolio_name=portfolio_name)

    ## Get Portfolio Breakdown
    df_portfolio_breakdown = cn.get_portfolio_breakdown(client, portfolio_uuid=portfolio_uuid)

    ## Get Current Positions using Mid-Price
    ## TODO: CHECK TO SEE IF THE MID-PRICE BEING CAPTURED IS ACCURATE FROM COINBASE
    current_positions = get_current_positions_from_portfolio(client, ticker_list=ticker_list,
                                                             portfolio_name=portfolio_name)

    ## Calculate the covariance matrix for tickers in the portfolio
    returns_cols = [f'{ticker}_t_1_close_pct_returns' for ticker in ticker_list]
    cov_matrix = df[returns_cols].rolling(rolling_cov_window).cov(pairwise=True).dropna()

    ## Delete rows prior to the first available date of the covariance matrix
    cov_matrix_start_date = cov_matrix.index.get_level_values(0).min()
    df = df[df.index >= cov_matrix_start_date]

    ## Derive the Daily Target Portfolio Volatility
    daily_target_volatility = annualized_target_volatility / np.sqrt(annual_trading_days)

    ## Reorder dataframe columns
    for ticker in ticker_list:
        df[f'{ticker}_new_position_size'] = 0.0
        df[f'{ticker}_new_position_notional'] = 0.0
        df[f'{ticker}_open_position_size'] = 0.0
        df[f'{ticker}_open_position_notional'] = 0.0
        df[f'{ticker}_actual_position_size'] = 0.0
        df[f'{ticker}_actual_position_notional'] = 0.0
        df[f'{ticker}_short_sale_proceeds'] = 0.0
        df[f'{ticker}_new_position_entry_exit_price'] = 0.0
        df[f'{ticker}_target_vol_normalized_weight'] = 0.0
        df[f'{ticker}_target_notional'] = 0.0
        df[f'{ticker}_target_size'] = 0.0
        df[f'{ticker}_cash_shrink_factor'] = 0.0
        df[f'{ticker}_stop_loss'] = 0.0
        df[f'{ticker}_stopout_flag'] = False
        df[f'{ticker}_cooldown_counter'] = 0.0
        df[f'{ticker}_event'] = np.nan
    ord_cols = size_bin.reorder_columns_by_ticker(df.columns, ticker_list)
    df = df[ord_cols]

    ## Portfolio Level Cash and Positions are all set to 0
    df['daily_portfolio_volatility'] = 0.0
    df['available_cash'] = 0.0
    df['count_of_positions'] = 0.0
    df['total_actual_position_notional'] = 0.0
    df['total_target_notional'] = 0.0
    df['total_portfolio_value'] = 0.0
    df['total_portfolio_value_upper_limit'] = 0.0
    df['target_vol_scaling_factor'] = 1.0
    df['cash_scaling_factor'] = 1.0
    df['cash_shrink_factor'] = 1.0
    df['final_scaling_factor'] = 1.0

    ## Cash and the Total Portfolio Value on Day 1 is the initial capital for the strategy
    if use_specific_start_date:
        start_index_position = df.index.get_loc(signal_start_date)
    else:
        start_index_position = 0
    # df['available_cash'][start_index_position] = initial_capital
    # df['total_portfolio_value'][start_index_position] = initial_capital

    ## Identify Daily Positions starting from day 2
    # for date in df.index[start_index_position + 1:]:
    previous_date = df.index[df.index.get_loc(date) - 1]

    ## Start the day with the available cash from portfolio
    df['available_cash'].loc[date] = available_cash  # df['available_cash'].loc[previous_date]

    ## Calculate Total Portfolio Value from Portfolio Positions
    short_sale_proceeds_cols = [f'{ticker}_short_sale_proceeds' for ticker in ticker_list]
    df['total_actual_position_notional'].loc[date] = portfolio_equity
    total_portfolio_value = (df['available_cash'].loc[date] +
                             df[short_sale_proceeds_cols].loc[date].sum() +
                             df['total_actual_position_notional'].loc[date])
    df['total_portfolio_value'].loc[date] = total_portfolio_value

    ## Update Total Portfolio Value Upper Limit based on the Total Portfolio Value
    total_portfolio_value_upper_limit = (df['total_portfolio_value'].loc[date] *
                                         (1 - cash_buffer_percentage))
    df['total_portfolio_value_upper_limit'].loc[date] = total_portfolio_value_upper_limit

    ## Calculate the target notional by ticker
    df = size_cont.get_target_volatility_position_sizing(df, cov_matrix, date, ticker_list, daily_target_volatility,
                                                         total_portfolio_value_upper_limit)

    ## Adjust Positions for Cash Available
    desired_positions, cash_shrink_factor = size_cont.get_cash_adjusted_desired_positions(
        df, date, previous_date, ticker_list, cash_buffer_percentage, transaction_cost_est, passive_trade_rate,
        total_portfolio_value, notional_threshold_pct, min_trade_notional_abs)

    ## Apply Cash Shrink Factor to Desired Positions
    for ticker in ticker_list:
        desired_positions[ticker]['new_trade_notional'] = desired_positions[ticker][
                                                              'new_trade_notional'] * cash_shrink_factor
        desired_positions[ticker]['trade_fees'] = desired_positions[ticker]['trade_fees'] * cash_shrink_factor

    return df, desired_positions, cash_shrink_factor

In [1018]:
datetime.now().date()

datetime.date(2025, 9, 18)

In [1026]:
end_date

datetime.date(2025, 9, 18)

In [1048]:
portfolio_equity

26900.189009257

In [1050]:
available_cash

45.306778

In [1052]:
df_portfolio_breakdown

asset                          account_uuid  \
0     AMP  0c34eeaf-64e5-5b2a-99a3-326747eefdda   
1    AVAX  0d4dc05a-5e31-5199-9b62-ac2df617e922   
2     MIR  16fba6c3-8838-5255-802f-b24f8ea16341   
3     GRT  1f554eec-0138-58d9-b407-d7868a7fac9a   
4    ALGO  33397cd1-85ce-5afc-ad4d-8db03e3e2b11   
5   MATIC  3565ae01-5192-5615-9100-f1ec125f5233   
6     KRL  3aacc4c7-3872-517e-b12c-f473d8d95ad3   
7     ETH  40a601d9-8ffa-500d-8f02-66d9123a2514   
8   COVAL  4fbb09a1-d130-5596-9040-7084e355d3b2   
9    ATOM  5b146b09-e11b-5fdb-a508-6db0e94b15dd   
10    USD  5d758151-9bd0-50f2-bda2-a8e9973cc40c   
11   AAVE  5f19d43d-43c1-5846-9251-dca0a1f90a8d   
12    OMG  69dd1aaf-bec3-526f-8747-127c287c6c3e   
13   SHIB  6c6d906b-c226-56a9-af48-3a8e6af3dedc   
14    SKL  6d13a728-fd68-5ddb-99b4-0f20c764c1b1   
15    UNI  74553a4b-f92c-59c3-882e-001deef5c028   
16    FET  7bcec305-590d-5b79-81c4-c2e06b2fc197   
17    DOT  7fbc87f4-3a18-5370-8433-094a834cc64e   
18   DOGE  89db83bc-e71b-5be4-91f1-f5e6bbe4cce5   
19    OXT  930f4b7f-660a-5b05-bcee-5d291edef3f1   
20    LTC  9520e7c6-a8d1-5175-9148-31ef28a31a9c   
21   MANA  95227930-a366-51d7-9b2e-c6e56fa42a98   
22    ADA  b03d98bb-9471-503d-ada1-e22a782bb509   
23    XLM  bddec0dc-6575-55d6-8290-8745aa5a5b0d   
24    RLY  bdf2c0e0-7b5b-5421-87b2-9b32a95e9d36   
25    DAI  cfd53591-1b1d-5770-b61f-30cfb5e76e32   
26    BTC  dd9f67c8-a344-55e1-8695-2d4e3a4e77e5   
27    SOL  e1475725-5f00-5746-bc35-1225b21849ca   
28    REQ  ed7bf5dc-5343-59b3-a7d8-dc4e5e57004c   
29    VGX  f4d17eab-fe1f-510b-be0c-9280556f6214   

                              asset_uuid  total_balance_fiat  \
0   f3b62870-ddd0-5dea-9d80-5190d8558461           17.332125   
1   9d06e463-b3ba-5abf-9082-8761846b28ab          373.878300   
2   3bd2e3bf-5923-5cc9-93df-8c23b92af4f4            0.855868   
3   3f9b015d-387d-589b-b65d-bd6d24babc96            0.250226   
4   9220d47f-bc0a-53ad-9646-ef49918adcf3          417.532650   
5   026bcc1e-9163-591c-a709-34dd18b2e7a1           62.729060   
6   015db578-d600-5613-8736-0eec500dfc4d           23.567602   
7   d85dce9b-5b73-5c3c-8978-522ce1d1c1b4        11614.039000   
8   d8816d7a-18c3-5385-b5c6-7cc0cfef9752            0.044528   
9   64c607d2-4663-5649-86e0-3ab06bba0202           55.482746   
10                                                 45.306778   
11  b1646860-6b23-5f7d-a506-cba0902f0ca9          639.345760   
12  7616bfa5-9874-5680-87ef-6f04dd3a0e75            0.032261   
13  d6031388-71ab-59c7-8a15-a56ec20d6080           54.567425   
14  af2d755d-6142-57f4-a092-0aa4fe67a9b5            0.467383   
15  412832ad-59dd-5af8-8d36-99ebda3afb80            0.000019   
16  3672ab4a-25e0-57a8-b029-99239c081958          228.571210   
17  ebea861a-c0ae-5323-bbe0-46893a119a39          306.935120   
18  d9a3edfa-1be7-589c-bd20-c034f3830b60           99.512490   
19  07525606-a404-5f15-a71d-ba0e40e74eca           38.827590   
20  c9c24c6e-c045-5fde-98a2-00ea7f520437          248.761630   
21  66b98195-0562-586b-8cee-ee7f57923fef           56.126930   
22  63062039-7afb-56ff-8e19-5e3215dc404a         1127.697000   
23  13b83335-5ede-595b-821e-5bcdfa80560f          225.230600   
24  39d7d62b-c1fc-5db4-bc0e-a0465473a748            0.196797   
25  01e9e33b-d099-56fb-aa3b-76c19d0b250e          347.032560   
26  5b71fc48-3dd3-540c-809b-f8c94d0e68b5         5935.408700   
27  4f039497-3af8-5bb3-951c-6df9afa9be1c         5016.950000   
28  7c6cf248-e06b-5426-a05d-ac2777159a11            8.775335   
29  6f45890a-c456-55da-bcfe-b10ced22818c            0.038094   

    available_to_trade_fiat  total_balance_crypto    allocation  \
0                 17.332125          5.060475e+03  6.432290e-04   
1                373.878300          1.144058e+01  1.387535e-02   
2                  0.000000          6.709501e+01  3.176292e-05   
3                  0.250226          2.579647e+00  9.286366e-06   
4                417.532650          1.711901e+03  1.549545e-02   
5                 62.729060        

In [1028]:
## Strategy Parameters
cfg = load_prod_strategy_config()
date = datetime.now().date()
portfolio_name = 'Default'#cfg['portfolio']['name']

df = df_signal
date = end_date
ticker_list = cfg['universe']['tickers']
initial_capital = cfg['run']['initial_capital']
rolling_cov_window = cfg['risk_and_sizing']['rolling_cov_window']
rolling_atr_window = cfg['risk_and_sizing']['rolling_atr_window']
atr_multiplier = cfg['risk_and_sizing']['atr_multiplier']
cash_buffer_percentage = cfg['risk_and_sizing']['cash_buffer_percentage']
annualized_target_volatility = cfg['risk_and_sizing']['annualized_target_volatility']
transaction_cost_est = cfg['execution_and_costs']['transaction_cost_est']
passive_trade_rate = cfg['execution_and_costs']['passive_trade_rate']
notional_threshold_pct = cfg['execution_and_costs']['notional_threshold_pct']
min_trade_notional_abs = cfg['execution_and_costs']['min_trade_notional_abs']
cooldown_counter_threshold = cfg['execution_and_costs']['cooldown_counter_threshold']
annual_trading_days = cfg['run']['annual_trading_days']
use_specific_start_date = False
signal_start_date = cfg['run']['signal_start_date']
portfolio_name = portfolio_name



df = get_strategy_trend_signal(cfg)
## Create Coinbase Client & Portfolio UUID
client = cn.get_coinbase_rest_api_client(portfolio_name=portfolio_name)
portfolio_uuid = cn.get_portfolio_uuid(client, portfolio_name=portfolio_name)

## Get Live Portfolio Equity
portfolio_equity, available_cash = get_live_portfolio_equity_and_cash(client=client, portfolio_name=portfolio_name)

## Get Portfolio Breakdown
df_portfolio_breakdown = cn.get_portfolio_breakdown(client, portfolio_uuid=portfolio_uuid)

## Get Current Positions using Mid-Price
## TODO: CHECK TO SEE IF THE MID-PRICE BEING CAPTURED IS ACCURATE FROM COINBASE
current_positions = get_current_positions_from_portfolio(client, ticker_list=ticker_list, portfolio_name=portfolio_name)

## Calculate the covariance matrix for tickers in the portfolio
returns_cols = [f'{ticker}_t_1_close_pct_returns' for ticker in ticker_list]
cov_matrix = df[returns_cols].rolling(rolling_cov_window).cov(pairwise=True).dropna()

## Delete rows prior to the first available date of the covariance matrix
cov_matrix_start_date = cov_matrix.index.get_level_values(0).min()
df = df[df.index >= cov_matrix_start_date]

## Derive the Daily Target Portfolio Volatility
daily_target_volatility = annualized_target_volatility / np.sqrt(annual_trading_days)

## Reorder dataframe columns
for ticker in ticker_list:
    df[f'{ticker}_new_position_size'] = 0.0
    df[f'{ticker}_new_position_notional'] = 0.0
    df[f'{ticker}_open_position_size'] = 0.0
    df[f'{ticker}_open_position_notional'] = 0.0
    df[f'{ticker}_actual_position_size'] = 0.0
    df[f'{ticker}_actual_position_notional'] = 0.0
    df[f'{ticker}_short_sale_proceeds'] = 0.0
    df[f'{ticker}_new_position_entry_exit_price'] = 0.0
    df[f'{ticker}_target_vol_normalized_weight'] = 0.0
    df[f'{ticker}_target_notional'] = 0.0
    df[f'{ticker}_target_size'] = 0.0
    df[f'{ticker}_cash_shrink_factor'] = 0.0
    df[f'{ticker}_stop_loss'] = 0.0
    df[f'{ticker}_stopout_flag'] = False
    df[f'{ticker}_cooldown_counter'] = 0.0
    df[f'{ticker}_event'] = np.nan
ord_cols = size_bin.reorder_columns_by_ticker(df.columns, ticker_list)
df = df[ord_cols]

## Portfolio Level Cash and Positions are all set to 0
df['daily_portfolio_volatility'] = 0.0
df['available_cash'] = 0.0
df['count_of_positions'] = 0.0
df['total_actual_position_notional'] = 0.0
df['total_target_notional'] = 0.0
df['total_portfolio_value'] = 0.0
df['total_portfolio_value_upper_limit'] = 0.0
df['target_vol_scaling_factor'] = 1.0
df['cash_scaling_factor'] = 1.0
df['cash_shrink_factor'] = 1.0
df['final_scaling_factor'] = 1.0

## Cash and the Total Portfolio Value on Day 1 is the initial capital for the strategy
if use_specific_start_date:
    start_index_position = df.index.get_loc(signal_start_date)
else:
    start_index_position = 0
# df['available_cash'][start_index_position] = initial_capital
# df['total_portfolio_value'][start_index_position] = initial_capital

## Identify Daily Positions starting from day 2
# for date in df.index[start_index_position + 1:]:
previous_date = df.index[df.index.get_loc(date) - 1]

## Start the day with the available cash from portfolio
df['available_cash'].loc[date] = available_cash#df['available_cash'].loc[previous_date]

## Calculate Total Portfolio Value from Portfolio Positions
short_sale_proceeds_cols = [f'{ticker}_short_sale_proceeds' for ticker in ticker_list]
df['total_actual_position_notional'].loc[date] = portfolio_equity
total_portfolio_value = (df['available_cash'].loc[date] +
                         df[short_sale_proceeds_cols].loc[date].sum() +
                         df['total_actual_position_notional'].loc[date])
df['total_portfolio_value'].loc[date] = total_portfolio_value

## Update Total Portfolio Value Upper Limit based on the Total Portfolio Value
total_portfolio_value_upper_limit = (df['total_portfolio_value'].loc[date] *
                                     (1 - cash_buffer_percentage))
df['total_portfolio_value_upper_limit'].loc[date] = total_portfolio_value_upper_limit

## Calculate the target notional by ticker
df = size_cont.get_target_volatility_position_sizing(df, cov_matrix, date, ticker_list, daily_target_volatility,
                                                     total_portfolio_value_upper_limit)

## Adjust Positions for Cash Available
desired_positions, cash_shrink_factor = size_cont.get_cash_adjusted_desired_positions(
    df, date, previous_date, ticker_list, cash_buffer_percentage, transaction_cost_est, passive_trade_rate,
    total_portfolio_value, notional_threshold_pct, min_trade_notional_abs)

## Apply Cash Shrink Factor to Desired Positions
for ticker in ticker_list:
    desired_positions[ticker]['new_trade_notional'] = desired_positions[ticker]['new_trade_notional'] * cash_shrink_factor
    desired_positions[ticker]['trade_fees'] = desired_positions[ticker]['trade_fees'] * cash_shrink_factor

/Users/adheerchauhan/Documents/git/trend_following/live_strategy/trend_following_strategy_v0.1.0-live/config/trend_strategy_config_v0.1.0.yaml
True
Generating Volatility Adjusted Trend Signal!!
Getting Average True Range for Stop Loss Calculation!!


In [1040]:
total_portfolio_value

26945.495787256998

In [1034]:
df.tail()

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2025-09-14                      2476.325115                               0.0   
2025-09-15                      2341.495104                               0.0   
2025-09-16                      2347.653666                               0.0   
2025-09-17                      2338.353316                               0.0   
2025-09-18                      2363.526334                               0.0   

            BTC-USD_actual_position_size  BTC-USD_annualized_volatility_30  \
date                                                                         
2025-09-14                           0.0                          0.307723   
2025-09-15                           0.0                          0.307100   
2025-09-16                           0.0                          0.307115   
2025-09-17                           0.0                          0.310471   
2025-09-18                           0.0                          0.308505   

            BTC-USD_cash_shrink_factor  BTC-USD_close  \
date                                                    
2025-09-14                         0.0      115314.13   
2025-09-15                         0.0      115381.08   
2025-09-16                         0.0      116832.56   
2025-09-17                         0.0      116484.40   
2025-09-18                         0.0      117131.54   

            BTC-USD_cooldown_counter  BTC-USD_event  BTC-USD_final_signal  \
date                                                                        
2025-09-14                       0.0            NaN                   0.0   
2025-09-15                       0.0            NaN                   0.0   
2025-09-16                       0.0            NaN                   0.0   
2025-09-17                       0.0            NaN                   0.0   
2025-09-18                       0.0            NaN                   0.0   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2025-09-14                               -0.409554   
2025-09-15                               -0.409382   
2025-09-16                               -0.408797   
2025-09-17                               -0.404303   
2025-09-18                               -0.400209   

            BTC-USD_new_position_entry_exit_price  \
date                                                
2025-09-14                                    0.0   
2025-09-15                                    0.0   
2025-09-16                                    0.0   
2025-09-17                                    0.0   
2025-09-18                                    0.0   

            BTC-USD_new_position_notional  BTC-USD_new_position_size  \
date                                                                   
2025-09-14                            0.0                        0.0   
2025-09-15                            0.0                        0.0   
2025-09-16                            0.0                        0.0   
2025-09-17                            0.0                        0.0   
2025-09-18                            0.0                        0.0   

            BTC-USD_open  BTC-USD_open_position_notional  \
date                                                       
2025-09-14     115968.33                             0.0   
2025-09-15     115314.12                             0.0   
2025-09-16     115381.07                             0.0   
2025-09-17     116832.56                             0.0   
2025-09-18     116484.40                             0.0   

            BTC-USD_open_position_size  BTC-USD_short_sale_proceeds  \
date                                                                  
2025-09-14                         0.0                          0.0   
2025-09-15                         0.0                          0.0

In [1044]:
new_trade_notional_sum = 0
for ticker in cfg['universe']['tickers']:
    new_trade_notional_sum += desired_positions[ticker]['new_trade_notional']

print(f'Total New Trade Notional: {new_trade_notional_sum}')
desired_positions

Total New Trade Notional: 40.7761002


{'BTC-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0},
 'ETH-USD': {'new_trade_notional': 11.25943886705028,
  'trade_fees': 0.14299487361153856},
 'SOL-USD': {'new_trade_notional': 14.283103970256485,
  'trade_fees': 0.18139542042225737},
 'ADA-USD': {'new_trade_notional': 7.459987362341815,
  'trade_fees': 0.09474183950174106},
 'AVAX-USD': {'new_trade_notional': 7.773570000351422,
  'trade_fees': 0.09872433900446306}}

In [1046]:
df_signal.tail()

BTC-USD_close  BTC-USD_open  BTC-USD_t_1_close  \
date                                                         
2025-09-14      115314.13     115968.33          115968.35   
2025-09-15      115381.08     115314.12          115314.13   
2025-09-16      116832.56     115381.07          115381.08   
2025-09-17      116484.40     116832.56          116832.56   
2025-09-18      117330.57     116484.40          116484.40   

            BTC-USD_t_1_close_pct_returns  BTC-USD_final_signal  \
date                                                              
2025-09-14                      -0.001186                   0.0   
2025-09-15                      -0.005641                   0.0   
2025-09-16                       0.000581                   0.0   
2025-09-17                       0.012580                   0.0   
2025-09-18                      -0.002980                   0.0   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2025-09-14                               -0.409554   
2025-09-15                               -0.409382   
2025-09-16                               -0.408797   
2025-09-17                               -0.404303   
2025-09-18                               -0.400209   

            BTC-USD_annualized_volatility_30  \
date                                           
2025-09-14                          0.307723   
2025-09-15                          0.307100   
2025-09-16                          0.307115   
2025-09-17                          0.310471   
2025-09-18                          0.308505   

            BTC-USD_vol_adjusted_trend_signal  ETH-USD_close  ETH-USD_open  \
date                                                                         
2025-09-14                                0.0        4605.93       4669.00   
2025-09-15                                0.0        4524.56       4605.93   
2025-09-16                                0.0        4502.70       4524.68   
2025-09-17                                0.0        4592.17       4502.70   
2025-09-18                                0.0        4588.01       4592.17   

            ETH-USD_t_1_close  ETH-USD_t_1_close_pct_returns  \
date                                                           
2025-09-14            4669.00                      -0.009685   
2025-09-15            4605.93                      -0.013508   
2025-09-16            4524.56                      -0.017666   
2025-09-17            4502.70                      -0.004831   
2025-09-18            4592.17                       0.019870   

            ETH-USD_final_signal  ETH-USD_final_weighted_additive_signal  \
date                                                                       
2025-09-14              0.317216                                0.349245   
2025-09-15              0.315698                                0.347843   
2025-09-16              0.309804                                0.342251   
2025-09-17              0.302844                                0.336200   
2025-09-18              0.300179                                0.333772   

            ETH-USD_annualized_volatility_30  \
date                                           
2025-09-14                          0.780180   
2025-09-15                          0.776800   
2025-09-16                          0.779588   
2025-09-17                          0.779059   
2025-09-18                          0.770145   

            ETH-USD_vol_adjusted_trend_signal  SOL-USD_close  SOL-USD_open  \
date                                                                         
2025-09-14                           0.406594         239.86        242.50   
2025-09-15                           0.406409         234.35        239.85   
2025-09-16                           0.397395         237.01        234.33   
2025-09-17                           0.388730         244.91        237.01   
2025-09-18                           0.389770         247

In [974]:
## Strategy Parameters
cfg = load_prod_strategy_config()
end_date = datetime.now().date
portfolio_name = 'Default'#cfg['portfolio']['name']
target_vol_kwargs = {
    "df": df_signal,
    "date": end_date,
    "ticker_list": cfg['universe']['tickers'],
    "initial_capital": cfg['run']['initial_capital'],
    "rolling_cov_window": cfg['risk_and_sizing']['rolling_cov_window'],
    "rolling_atr_window": cfg['risk_and_sizing']['rolling_atr_window'],
    "atr_multiplier": cfg['risk_and_sizing']['atr_multiplier'],
    "cash_buffer_percentage": cfg['risk_and_sizing']['cash_buffer_percentage'],
    "annualized_target_volatility": cfg['risk_and_sizing']['annualized_target_volatility'],
    "transaction_cost_est": cfg['execution_and_costs']['transaction_cost_est'],
    "passive_trade_rate": cfg['execution_and_costs']['passive_trade_rate'],
    "notional_threshold_pct": cfg['execution_and_costs']['notional_threshold_pct'],
    "min_trade_notional_abs": cfg['execution_and_costs']['min_trade_notional_abs'],
    "cooldown_counter_threshold": cfg['execution_and_costs']['cooldown_counter_threshold'],
    "annual_trading_days": cfg['run']['annual_trading_days'],
    "use_specific_start_date": False,
    "signal_start_date": cfg['run']['signal_start_date'],
    "portfolio_name": portfolio_name
}

df_target_notional, desired_trades, cash_shrink_factor = get_target_notional_by_ticker(**target_vol_kwargs)

/Users/adheerchauhan/Documents/git/trend_following/live_strategy/trend_following_strategy_v0.1.0-live/config/trend_strategy_config_v0.1.0.yaml
True


KeyError: <built-in method date of datetime.datetime object at 0x17f598e70>

In [976]:
new_trade_notional_sum = 0
for ticker in cfg['universe']['tickers']:
    new_trade_notional_sum += desired_trades[ticker]['new_trade_notional']

print(f'Total New Trade Notional: {new_trade_notional_sum}')
desired_trades

Total New Trade Notional: 900.0


{'BTC-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0},
 'ETH-USD': {'new_trade_notional': 248.51555030133193,
  'trade_fees': 3.156147488826915},
 'SOL-USD': {'new_trade_notional': 315.25313873029074,
  'trade_fees': 4.003714861874692},
 'ADA-USD': {'new_trade_notional': 164.6549962643959,
  'trade_fees': 2.091118452557828},
 'AVAX-USD': {'new_trade_notional': 171.57631470398144,
  'trade_fees': 2.179019196740564}}

In [978]:
df_target_notional.shape

(280, 136)

In [970]:
df_target_notional.tail()

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2025-09-14                      2476.325115                               0.0   
2025-09-15                      2341.495104                               0.0   
2025-09-16                      2347.653666                               0.0   
2025-09-17                      2338.353316                               0.0   
2025-09-18                      2363.526334                               0.0   

            BTC-USD_actual_position_size  BTC-USD_annualized_volatility_30  \
date                                                                         
2025-09-14                           0.0                          0.307723   
2025-09-15                           0.0                          0.307100   
2025-09-16                           0.0                          0.307115   
2025-09-17                           0.0                          0.310471   
2025-09-18                           0.0                          0.308505   

            BTC-USD_cash_shrink_factor  BTC-USD_close  \
date                                                    
2025-09-14                         0.0      115314.13   
2025-09-15                         0.0      115381.08   
2025-09-16                         0.0      116832.56   
2025-09-17                         0.0      116484.40   
2025-09-18                         0.0      116751.21   

            BTC-USD_cooldown_counter  BTC-USD_event  BTC-USD_final_signal  \
date                                                                        
2025-09-14                       0.0            NaN                   0.0   
2025-09-15                       0.0            NaN                   0.0   
2025-09-16                       0.0            NaN                   0.0   
2025-09-17                       0.0            NaN                   0.0   
2025-09-18                       0.0            NaN                   0.0   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2025-09-14                               -0.409554   
2025-09-15                               -0.409382   
2025-09-16                               -0.408797   
2025-09-17                               -0.404303   
2025-09-18                               -0.400209   

            BTC-USD_new_position_entry_exit_price  \
date                                                
2025-09-14                                    0.0   
2025-09-15                                    0.0   
2025-09-16                                    0.0   
2025-09-17                                    0.0   
2025-09-18                                    0.0   

            BTC-USD_new_position_notional  BTC-USD_new_position_size  \
date                                                                   
2025-09-14                            0.0                        0.0   
2025-09-15                            0.0                        0.0   
2025-09-16                            0.0                        0.0   
2025-09-17                            0.0                        0.0   
2025-09-18                            0.0                        0.0   

            BTC-USD_open  BTC-USD_open_position_notional  \
date                                                       
2025-09-14     115968.33                             0.0   
2025-09-15     115314.12                             0.0   
2025-09-16     115381.07                             0.0   
2025-09-17     116832.56                             0.0   
2025-09-18     116484.40                             0.0   

            BTC-USD_open_position_size  BTC-USD_short_sale_proceeds  \
date                                                                  
2025-09-14                         0.0                          0.0   
2025-09-15                         0.0                          0.0

## Build Coinbase Code to Send Orders with the Desired Trades

In [627]:
cn_client.get_product(product_id)

{'product_id': 'ETH-USD', 'price': '4644.39', 'price_percentage_change_24h': '0.31643245625024', 'volume_24h': '139769.69866917', 'volume_percentage_change_24h': '-2.6439761366706', 'base_increment': '0.00000001', 'quote_increment': '0.01', 'quote_min_size': '1', 'quote_max_size': '150000000', 'base_min_size': '0.00000001', 'base_max_size': '42000', 'base_name': 'Ethereum', 'quote_name': 'US Dollar', 'watched': True, 'is_disabled': False, 'new': False, 'status': 'online', 'cancel_only': False, 'limit_only': False, 'post_only': False, 'trading_disabled': False, 'auction_mode': False, 'product_type': 'SPOT', 'quote_currency_id': 'USD', 'base_currency_id': 'ETH', 'fcm_trading_session_details': None, 'mid_market_price': '', 'alias': '', 'alias_to': ['ETH-USDC'], 'base_display_symbol': 'ETH', 'quote_display_symbol': 'USD', 'view_only': False, 'price_increment': '0.01', 'display_name': 'ETH-USD', 'product_venue': 'CBE', 'approximate_quote_24h_volume': '649144990.8', 'new_at': '2023-01-01T00:

In [609]:
import math, time, uuid
from typing import Dict, Any

def get_product_meta(client, product_id: str):
    """
    Returns increments & mins for sizing/price rounding.
    """
    p = client.get_product(product_id)  # Advanced Trade: /api/v3/brokerage/products/{product_id}
    # Public/List Public Products also exposes similar fields.
    # Fields include base_increment, quote_increment, base_min_size, quote_min_size, price_increment, etc.
    return {
        "base_increment": float(p.base_increment),                                                    ## Minimum amount base value can be increased or decreased at once.
        "quote_increment": float(p.quote_increment) if getattr(p, "quote_increment", None) else None, ## Minimum amount quote value can be increased or decreased at once
        "base_min_size": float(p.base_min_size),                                                      ## Minimum size that can be represented of base currency
        "quote_min_size": float(p.quote_min_size) if getattr(p, "quote_min_size", None) else None,    ## Minimum size that can be represented of quote currency
        "price_increment": float(p.price_increment) if getattr(p, "price_increment", None) else None, ## Minimum amount price can be increased or decreased at once
    }

In [611]:
def round_down(x, step):
    if step is None or step == 0:
        return x
    return math.floor(x / step) * step

def round_to_increment(x, step):
    # For prices it’s usually exact multiples; round to nearest multiple.
    if step is None or step == 0:
        return x
    return round(round(x / step) * step, int(max(0, -math.log10(step))))

def current_mid(client, product_id):
    """
    Safer 'now' price: use Best Bid/Ask midpoint.
    """
    bba = client.get_best_bid_ask([product_id]).pricebooks[0]
    bid = float(bba['bids'][0]['price'])
    ask = float(bba['asks'][0]['price'])
    return (bid + ask) / 2.0

In [639]:
## Base = the asset you’re buying/selling (first symbol in the pair).
## For BTC-USD, the base is BTC. Quantities in base are “units of the coin.”
## Quote = the currency you price the trade in (second symbol).
## For BTC-USD, the quote is USD. Prices and notional values are in quote.
## Coinbase expects USD amount you want to spend for Buy Orders
## Coinbase expects crypto units to sell for Sell Orders

def build_order_params(product_id,
                       new_trade_notional,  # USD (+ buy, - sell) from your desired_positions[t]['new_trade_notional']
                       px_now, meta):
    """
    Returns dict with side and the correct size param, already quantized to increments and mins.
    """
    if new_trade_notional > 0:
        side = "BUY"
        quote_size_raw = abs(new_trade_notional)
        # Enforce min & increment on QUOTE
        quote_size = max(quote_size_raw, meta["quote_min_size"] or 0.0)
        # Some products only enforce funds minimums; quote_increment may be None.
        if meta["quote_increment"]:
            quote_size = round_down(quote_size, meta["quote_increment"])
        if quote_size <= 0:
            return {}
        return {"side": side, "quote_size": f"{quote_size:.8f}"}
    elif new_trade_notional < 0:
        side = "SELL"
        base_size_raw = abs(new_trade_notional) / px_now
        # Enforce min & increment on BASE
        base_size = max(base_size_raw, meta["base_min_size"])
        base_size = round_down(base_size, meta["base_increment"])
        if base_size <= 0:
            return {}
        return {"side": side, "base_size": f"{base_size:.8f}"}
    else:
        return {}

In [595]:
from coinbase.rest import RESTClient

def place_primary_order(client: RESTClient,
                        product_id: str,
                        side: str,
                        quote_size: str | None,
                        base_size: str | None,
                        portfolio_id: str) -> dict:
    """
    Submit a market order. BUY: quote_size; SELL: base_size.
    """
    client_order_id = str(uuid.uuid4())
    # Optional: preview first
    try:
        if side == "BUY":
            client.preview_market_order_buy(
                product_id=product_id,
                quote_size=quote_size,
                retail_portfolio_id=portfolio_id
            )
        else:
            client.preview_market_order_sell(
                product_id=product_id,
                base_size=base_size,
                retail_portfolio_id=portfolio_id
            )
    except Exception as e:
        raise RuntimeError(f"Preview failed for {product_id} {side}: {e}")

    # Send the live order
    if side == "BUY":
        resp = client.market_order_buy(
            client_order_id=client_order_id,
            product_id=product_id,
            quote_size=quote_size,
            retail_portfolio_id=portfolio_id
        )
    else:
        resp = client.market_order_sell(
            client_order_id=client_order_id,
            product_id=product_id,
            base_size=base_size,
            retail_portfolio_id=portfolio_id
        )

    return {"client_order_id": client_order_id, "response": resp}


In [631]:
meta = get_product_meta(cn_client, product_id='ETH-USD')
px_now = current_mid(cn_client, product_id='ETH-USD')
build_order_params(product_id='ETH-USD', new_trade_notional=desired_trades['ETH-USD']['new_trade_notional'], meta=meta, px_now=px_now)

{'side': 'BUY', 'quote_size': '402.33000000'}

In [632]:
client_order_id = str(uuid.uuid4())
product_id = 'ETH-USD'
meta_eth = get_product_meta(cn_client, product_id=product_id)
eth_px_now = current_mid(cn_client, product_id=product_id)
quote_size = build_order_params(product_id=product_id, new_trade_notional=desired_trades[product_id]['new_trade_notional'],
                               meta=meta_eth, px_now=eth_px_now)

In [635]:
quote_size

{'side': 'BUY', 'quote_size': '402.33000000'}

In [637]:
meta_eth

{'base_increment': 1e-08,
 'quote_increment': 0.01,
 'base_min_size': 1e-08,
 'quote_min_size': 1.0,
 'price_increment': 0.01}

In [581]:
portfolio_id = cn.get_portfolio_uuid(client=cn_client, portfolio_name=cfg['portfolio']['name'])

In [603]:
cn_client.preview_market_order_buy(product_id=product_id, quote_size=quote_size['quote_size'], retail_portfolio_id=portfolio_id)

{'order_total': '402.3299999999999999852', 'commission_total': '4.7707114624505928852', 'errs': [], 'warning': [], 'quote_size': '397.5592885375494071', 'base_size': '0.0856560007309402', 'best_bid': '4641.29', 'best_ask': '4641.3', 'is_max': False, 'order_margin_total': '0', 'leverage': '0', 'long_leverage': '0', 'short_leverage': '0', 'slippage': '0.0000102936723016', 'preview_id': '83433578-8d82-4c17-a74a-731e831b1367', 'current_liquidation_buffer': '0', 'projected_liquidation_buffer': '0', 'max_leverage': '', 'pnl_configuration': None, 'twap_bucket_metadata': None, 'position_notional_limit': '', 'max_notional_at_requested_leverage': '', 'margin_ratio_data': {'current_margin_ratio': '0', 'projected_margin_ratio': '0'}, 'commission_detail_total': {'total_commission': '4.7707114624505928852', 'gst_commission': '0', 'withholding_commission': '0', 'client_commission': '4.7707114624505928852'}, 'scaled_metadata': None}

In [599]:
cn_client.preview_market_order_sell(product_id=product_id, base_size=quote_size['quote_size'], retail_portfolio_id=portfolio_id)

{'order_total': '1841514.4170512111412', 'commission_total': '22366.5718670187588', 'errs': ['PREVIEW_INSUFFICIENT_FUND'], 'warning': [], 'quote_size': '1863880.9889182299', 'base_size': '402.33', 'best_bid': '4637.09', 'best_ask': '4637.1', 'is_max': False, 'order_margin_total': '0', 'leverage': '0', 'long_leverage': '0', 'short_leverage': '0', 'slippage': '0.0009439609032073', 'preview_id': '2c74f157-9618-4be7-be65-c937ea5ebf9a', 'current_liquidation_buffer': '0', 'projected_liquidation_buffer': '0', 'max_leverage': '', 'pnl_configuration': None, 'twap_bucket_metadata': None, 'position_notional_limit': '', 'max_notional_at_requested_leverage': '', 'margin_ratio_data': {'current_margin_ratio': '0', 'projected_margin_ratio': '0'}, 'commission_detail_total': {'total_commission': '22366.5718670187588', 'gst_commission': '0', 'withholding_commission': '0', 'client_commission': '22366.5718670187588'}, 'scaled_metadata': None}

## Setting up Test Script to Automatically Pull CLose and Open Prices Daily

In [646]:
pathlib.Path(os.environ.get("PRICE_SNAPSHOT_DIR", "~/Documents/git/trend_following/data_folder/coinbase_daily")).expanduser()

PosixPath('/Users/adheerchauhan/Documentsgit/trend_following/data_folder/coinbase_daily')

In [650]:
r = requests.get(f"{BASE}/time", timeout=10)
r.raise_for_status()
js = r.json()

In [656]:
r.raise_for_status()

In [654]:
js

{'iso': '2025-09-14T16:24:40Z',
 'epochSeconds': '1757867080',
 'epochMillis': '1757867080044'}

In [668]:
flag = DONE_FLAG_DIR / f"{today_date}.done"
flag.exists()

False

In [674]:
now = get_server_time_utc()  # Coinbase server time (UTC)
today_date = now.date()      # UTC date
# Gate: only run between 00:01–00:15 UTC; else exit quietly.
if not (now.hour == 0 and 1 <= now.minute <= 15):
    print("Time False")
    # return

flag = DONE_FLAG_DIR / f"{today_date}.done"
if flag.exists():
    print("False")
    # return  # already ran today

rows = []
for pid in UNIVERSE:
    yday = get_yday_daily(pid, today_date)
    # retry a couple times if the 1m candle isn't posted yet
    t_open = None
    for _ in range(6):  # up to ~3 minutes
        t_open = get_today_open(pid, today_date)
        if t_open:
            break
        time.sleep(30)

    rows.append({
        "product_id": pid,
        "date_utc": str(today_date),
        "yday_open": yday["yday_open"] if yday else None,
        "yday_close": yday["yday_close"] if yday else None,
        "today_open_utc": t_open["today_open"] if t_open else None,
    })

df = pd.DataFrame(rows)
run_ts = dt.datetime.now(dt.timezone.utc)
snap_name = f"opens_closes_{today_date}_{run_ts.strftime('%H%M%SZ')}.csv"
out_path = SNAP_DIR / snap_name
df.to_csv(out_path, index=False)

# keep an append-only parquet table for analytics
# try:
#     if APPEND_PATH.exists():
#         old = pd.read_parquet(APPEND_PATH)
#         all_df = pd.concat([old, df], ignore_index=True)
#         # drop duplicates on (date_utc, product_id)
#         all_df = all_df.drop_duplicates(subset=["date_utc", "product_id"], keep="last")
#         all_df.to_parquet(APPEND_PATH, index=False)
#     else:
#         df.to_parquet(APPEND_PATH, index=False)
# except Exception as e:
#     # don't fail the run if parquet is unavailable
#     print("Parquet append failed:", e)

flag.touch()
print(f"Saved {len(df)} rows to {out_path}")

Time False
Saved 5 rows to /Users/adheerchauhan/Documents/coinbase_daily/snapshots/opens_closes_2025-09-14_163103Z.csv


In [676]:
get_server_time_utc()

datetime.datetime(2025, 9, 14, 16, 43, 8, tzinfo=datetime.timezone.utc)

In [678]:
os.environ.get("PRICE_SNAPSHOT_DIR", "~/Documents/git/trend_following/data_folder/coinbase_daily")

'~/Documents/git/trend_following/data_folder/coinbase_daily'

In [796]:
#!/usr/bin/env python3
import os, time, json, pathlib, requests, datetime as dt
import pandas as pd

BASE = "https://api.coinbase.com/api/v3/brokerage"
HEADERS = {"Cache-Control": "no-cache", "User-Agent": "tf-daily-opens/1.0"}  # bypass 1s cache; be nice to servers
UNIVERSE = ["BTC-USD", "ETH-USD", "SOL-USD", "ADA-USD", "AVAX-USD"]  # edit as needed

# ---- storage config ----
BASE_DIR = pathlib.Path(os.environ.get("PRICE_SNAPSHOT_DIR", "~/Documents/git/trend_following/data_folder/coinbase_daily")).expanduser()
SNAP_DIR = BASE_DIR / "snapshots"
APPEND_PATH = BASE_DIR / "daily_opens_closes.parquet"
DONE_FLAG_DIR = BASE_DIR / "done_flags"       # to avoid double-runs

SNAP_DIR.mkdir(parents=True, exist_ok=True)
DONE_FLAG_DIR.mkdir(parents=True, exist_ok=True)

def get_server_time_utc():
    r = requests.get(f"{BASE}/time", timeout=10)
    r.raise_for_status()
    js = r.json()
    # API returns iso and epoch strings
    return dt.datetime.fromtimestamp(int(js["epochSeconds"]), dt.timezone.utc)

def epoch(dt_utc):
    return int(dt_utc.replace(tzinfo=dt.timezone.utc).timestamp())

def bucket_bounds_utc(day_utc):
    start = dt.datetime(day_utc.year, day_utc.month, day_utc.day, tzinfo=dt.timezone.utc)
    end   = start + dt.timedelta(days=1)
    return start, end

def fetch_candles(product_id, start_utc, end_utc, granularity):
    params = {
        "start": str(epoch(start_utc)),
        "end": str(epoch(end_utc)),
        "granularity": granularity,  # ONE_DAY or ONE_MINUTE
        "limit": "350"
    }
    url = f"{BASE}/market/products/{product_id}/candles"
    for attempt in range(3):
        resp = requests.get(url, params=params, headers=HEADERS, timeout=15)
        if resp.status_code == 429:
            time.sleep(1.5 * (attempt + 1))
            continue
        resp.raise_for_status()
        js = resp.json()
        candles = js.get("candles", []) or []
        # Normalize order: oldest -> newest
        candles.sort(key=lambda c: int(c["start"]))
        return candles
    return []

def get_yday_daily(product_id, today_utc_date):
    """
    Return yesterday's daily open/close for product_id.

    Strategy:
      1) Ask for the ONE_DAY candle whose start == yesterday 00:00:00 UTC.
      2) If missing/empty, fall back to ONE_MINUTE candles over [00:00, 24:00):
         open = first 1m candle's open; close = last 1m candle's close.
    """
    yday = today_utc_date - dt.timedelta(days=1)
    y_start, y_end = bucket_bounds_utc(yday)
    y_start_epoch = epoch(y_start)
    y_end_epoch   = epoch(y_end)

    # --- Primary: daily candle at exactly yesterday 00:00Z ---
    daily = fetch_candles(product_id, y_start, y_end + dt.timedelta(seconds=1), "ONE_DAY")  # tiny end buffer
    if daily:
        # ensure oldest→newest in case fetch_candles doesn't already do this
        daily.sort(key=lambda c: int(c["start"]))
        # exact midnight match first
        pick = next((c for c in daily if int(c["start"]) == y_start_epoch), None)
        if pick is None:
            # otherwise any candle that starts within [start, end)
            elig = [c for c in daily if y_start_epoch <= int(c["start"]) < y_end_epoch]
            pick = elig[0] if elig else None
        if pick is not None:
            return {
                "yday_start": dt.datetime.fromtimestamp(int(pick["start"]), dt.timezone.utc),
                "yday_open":  float(pick["open"]),
                "yday_close": float(pick["close"]),
            }

    # --- Fallback: derive from 1-minute candles over the day ---
    one_min = fetch_candles(product_id, y_start, y_end, "ONE_MINUTE")
    if not one_min:
        return None  # nothing to do (exchange delay or network issue)

    one_min.sort(key=lambda c: int(c["start"]))  # oldest→newest
    first_c = one_min[0]
    last_c  = one_min[-1]
    return {
        "yday_start": dt.datetime.fromtimestamp(int(first_c["start"]), dt.timezone.utc),
        "yday_open":  float(first_c["open"]),
        "yday_close": float(last_c["close"]),
    }

def get_today_open(product_id, today_utc_date):
    s, _ = bucket_bounds_utc(today_utc_date)
    s_epoch = epoch(s)
    deadline = dt.datetime.now(dt.timezone.utc) + dt.timedelta(minutes=3)  # hard stop

    while dt.datetime.now(dt.timezone.utc) < deadline:
        candles = fetch_candles(product_id, s, s + dt.timedelta(minutes=2), "ONE_MINUTE")  # small window
        if candles:
            candles.sort(key=lambda c: int(c["start"]))  # oldest→newest
            pick = next((c for c in candles if int(c["start"]) == s_epoch), None)
            if pick:
                return {
                    "today_open_time": dt.datetime.fromtimestamp(int(pick["start"]), dt.timezone.utc),
                    "today_open": float(pick["open"])
                }
        time.sleep(2)  # tight poll to minimize delay
    return None


def main():
    now = get_server_time_utc()  # Coinbase server time (UTC)
    today_date = now.date()      # UTC date
    # Gate: only run between 00:01–00:15 UTC; else exit quietly.
    if not (now.hour == 0 and 1 <= now.minute <= 15):
        return

    flag = DONE_FLAG_DIR / f"{today_date}.done"
    if flag.exists():
        return  # already ran today

    rows = []
    for pid in UNIVERSE:
        yday = get_yday_daily(pid, today_date)
        # retry a couple times if the 1m candle isn't posted yet
        t_open = None
        for _ in range(6):  # up to ~3 minutes
            t_open = get_today_open(pid, today_date)
            if t_open:
                break
            time.sleep(30)

        rows.append({
            "product_id": pid,
            "date_utc": str(today_date),
            "yday_open": yday["yday_open"] if yday else None,
            "yday_close": yday["yday_close"] if yday else None,
            "today_open_utc": t_open["today_open"] if t_open else None,
        })

    df = pd.DataFrame(rows)
    run_ts = dt.datetime.now(dt.timezone.utc)
    snap_name = f"opens_closes_{today_date}_{run_ts.strftime('%H%M%SZ')}.csv"
    out_path = SNAP_DIR / snap_name
    df.to_csv(out_path, index=False)

    # keep an append-only parquet table for analytics
    try:
        if APPEND_PATH.exists():
            old = pd.read_parquet(APPEND_PATH)
            all_df = pd.concat([old, df], ignore_index=True)
            # drop duplicates on (date_utc, product_id)
            all_df = all_df.drop_duplicates(subset=["date_utc", "product_id"], keep="last")
            all_df.to_parquet(APPEND_PATH, index=False)
        else:
            df.to_parquet(APPEND_PATH, index=False)
    except Exception as e:
        # don't fail the run if parquet is unavailable
        print("Parquet append failed:", e)

    flag.touch()
    print(f"Saved {len(df)} rows to {out_path}")

if __name__ == "__main__":
    main()


In [872]:
FORCE_RUN = os.environ.get("FORCE_RUN") == "1"

In [874]:
FORCE_RUN

False

In [828]:
os.environ["MAIL_TO"]

KeyError: 'MAIL_TO'

In [830]:
import sys, datetime as dt
print(f"[{dt.datetime.utcnow().isoformat()}Z] using: {sys.executable}", flush=True)

[2025-09-17T02:02:17.324745Z] using: /opt/anaconda3/envs/crypto_prod/bin/python


In [870]:
dt.datetime.now(dt.timezone.UTC)

AttributeError: type object 'datetime.timezone' has no attribute 'UTC'

In [868]:
dt.datetime.now(dt.timezone.utc)

datetime.datetime(2025, 9, 17, 2, 7, 37, 668512, tzinfo=datetime.timezone.utc)

In [ ]:
(base) adheerchauhan@Macmini ~ % crontab -e

MAILTO=chauhan4@gmail.com
SHELL=/bin/bash

# Fire exactly at local times that map to 00:00 UTC year-round
0 19 * * * /bin/bash -lc "$HOME/bin/daily_coinbase_notify.sh"
0 20 * * * /bin/bash -lc "$HOME/bin/daily_coinbase_notify.sh"


In [884]:
now = get_server_time_utc()  # Coinbase server time (UTC)
today_date = now.date()      # UTC date
get_yday_daily(product_id='BTC-USD', today_utc_date=today_date)

{'yday_start': datetime.datetime(2025, 9, 17, 0, 0, tzinfo=datetime.timezone.utc),
 'yday_open': 116832.56,
 'yday_close': 116484.4}

In [886]:
today_date

datetime.date(2025, 9, 18)

In [888]:
FORCE_RUN = os.environ.get("FORCE_RUN") == "1"

In [890]:
FORCE_RUN

False

In [898]:
now.isoformat()

'2025-09-18T01:30:00+00:00'

In [800]:
now = get_server_time_utc()  # Coinbase server time (UTC)
today_date = now.date()      # UTC date
# Gate: only run between 00:01–00:15 UTC; else exit quietly.
# if not (now.hour == 0 and 1 <= now.minute <= 15):
#     return

flag = DONE_FLAG_DIR / f"{today_date}.done"
# if flag.exists():
#     return  # already ran today

rows = []
for pid in UNIVERSE:
    yday = get_yday_daily(pid, today_date)
    # retry a couple times if the 1m candle isn't posted yet
    t_open = None
    for _ in range(6):  # up to ~3 minutes
        t_open = get_today_open(pid, today_date)
        if t_open:
            break
        time.sleep(30)

    rows.append({
        "product_id": pid,
        "date_utc": str(today_date),
        "yday_open": yday["yday_open"] if yday else None,
        "yday_close": yday["yday_close"] if yday else None,
        "today_open_utc": t_open["today_open"] if t_open else None,
    })

df = pd.DataFrame(rows)

In [802]:
df

product_id    date_utc    yday_open   yday_close  today_open_utc
0    BTC-USD  2025-09-16  115314.1200  115381.0800     115381.0700
1    ETH-USD  2025-09-16    4605.9300    4524.5600       4524.6800
2    SOL-USD  2025-09-16     239.8500     234.3500        234.3300
3    ADA-USD  2025-09-16       0.8883       0.8635          0.8634
4   AVAX-USD  2025-09-16      29.4500      29.8100         29.8200

In [782]:
end_date

datetime.date(2025, 9, 15)

In [818]:
df_close = cn.save_historical_crypto_prices_from_coinbase(ticker='AVAX-USD', user_start_date=True, start_date=start_date,
                                                          end_date=pd.Timestamp('2025-09-16').date(), save_to_file=False)

In [820]:
df_close.tail()

low   high   open  close        volume
date                                                
2025-09-12  28.24  29.42  29.17  29.01  9.492642e+05
2025-09-13  28.77  31.27  29.01  30.11  1.526945e+06
2025-09-14  28.98  30.65  30.10  29.47  7.922918e+05
2025-09-15  28.26  30.43  29.45  29.81  1.389493e+06
2025-09-16  29.33  29.89  29.82  29.39  1.296060e+05

In [876]:
now = get_server_time_utc()  # Coinbase server time (UTC)
today_date = now.date()      # UTC date

In [877]:
today_date

datetime.date(2025, 9, 18)

In [880]:
s, e = bucket_bounds_utc(today_date)
# first 1m candle of the day
product_id = 'BTC-USD'
candles = fetch_candles(product_id, s, s + dt.timedelta(minutes=1), "ONE_MINUTE")

In [882]:
candles

[{'start': '1758153600',
  'low': '116429.44',
  'high': '116499.21',
  'open': '116484.4',
  'close': '116445.3',
  'volume': '10.19979674'},
 {'start': '1758153660',
  'low': '116373.83',
  'high': '116446.89',
  'open': '116445.3',
  'close': '116373.83',
  'volume': '3.89863049'}]

In [738]:
candles

[{'start': '1757980860',
  'low': '115349.21',
  'high': '115378.78',
  'open': '115368.32',
  'close': '115349.22',
  'volume': '0.89713597'},
 {'start': '1757980800',
  'low': '115362.29',
  'high': '115387.67',
  'open': '115381.07',
  'close': '115370.01',
  'volume': '2.32677377'}]

In [724]:
candles

[{'start': '1757894460',
  'low': '115188.07',
  'high': '115291.9',
  'open': '115291.9',
  'close': '115227.52',
  'volume': '11.69281546'},
 {'start': '1757894400',
  'low': '115236.01',
  'high': '115318.49',
  'open': '115314.12',
  'close': '115291.9',
  'volume': '9.9115587'}]

In [740]:
df_close.tail()

low       high       open      close       volume
date                                                               
2025-09-11  113433.92  115554.53  113983.98  115540.00  5575.360741
2025-09-12  114774.19  116833.25  115540.01  116106.03  6493.576328
2025-09-13  115177.53  116378.04  116106.03  115968.35  2173.496518
2025-09-14  115166.00  116226.61  115968.33  115314.13  1967.886838
2025-09-15  114642.00  116802.00  115314.12  114782.00  2275.466258

In [720]:
print(s)
print(e)

2025-09-15 00:00:00+00:00
2025-09-16 00:00:00+00:00


In [ ]:
candles = fetch_candles(product_id, s, s + dt.timedelta(minutes=1), "ONE_MINUTE")

In [684]:
!echo $HOME

/Users/adheerchauhan


In [686]:
Path.home()

PosixPath('/Users/adheerchauhan')

In [688]:
get_server_time_utc()

datetime.datetime(2025, 9, 15, 10, 44, 44, tzinfo=datetime.timezone.utc)

In [593]:
402.3299999999999999852/4.7707114624505928852

84.33333333333333

In [515]:
desired_trades['ETH-USD']['new_trade_notional']

19.812300986990994

In [507]:
px_now

4656.515

In [503]:
meta

{'base_inc': 1e-08,
 'quote_inc': 0.01,
 'base_min': 1e-08,
 'quote_min': 1.0,
 'price_inc': 0.01}

In [499]:
desired_trades

{'BTC-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0},
 'ETH-USD': {'new_trade_notional': 19.812300986990994,
  'trade_fees': 0.2516162225347856},
 'SOL-USD': {'new_trade_notional': 12.96371398745426,
  'trade_fees': 0.1646391676406691},
 'ADA-USD': {'new_trade_notional': 5.136888295593332,
  'trade_fees': 0.0652384813540353},
 'AVAX-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0}}

In [493]:
get_product_meta(cn_client, product_id='BTC-USD')

{'base_inc': 1e-08,
 'quote_inc': 0.01,
 'base_min': 1e-08,
 'quote_min': 1.0,
 'price_inc': 0.01}

In [495]:
current_mid(cn_client, product_id='BTC-USD')

115916.11499999999

In [400]:
df_target_notional[target_notional_cols].tail()

BTC-USD_target_notional  ETH-USD_target_notional  \
date                                                           
2025-09-09                      0.0                 0.000000   
2025-09-10                      0.0                 0.000000   
2025-09-11                      0.0                 0.000000   
2025-09-12                      0.0                 0.000000   
2025-09-13                      0.0             10931.645909   

            SOL-USD_target_notional  ADA-USD_target_notional  \
date                                                           
2025-09-09                 0.000000                 0.000000   
2025-09-10                 0.000000                 0.000000   
2025-09-11                 0.000000                 0.000000   
2025-09-12                 0.000000                 0.000000   
2025-09-13              7152.865841              2834.332264   

            AVAX-USD_target_notional  
date                                  
2025-09-09                  0.000000  
2025-09-10                  0.000000  
2025-09-11                  0.000000  
2025-09-12                  0.000000  
2025-09-13               1579.799087

In [402]:
df_target_notional[vol_adj_signal_cols].tail()

BTC-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-09                                0.0   
2025-09-10                                0.0   
2025-09-11                                0.0   
2025-09-12                                0.0   
2025-09-13                                0.0   

            ETH-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-09                           0.387070   
2025-09-10                           0.381193   
2025-09-11                           0.375356   
2025-09-12                           0.397460   
2025-09-13                           0.397160   

            SOL-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-09                           0.319970   
2025-09-10                           0.342137   
2025-09-11                           0.366026   
2025-09-12                           0.320871   
2025-09-13                           0.259873   

            ADA-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-09                           0.119856   
2025-09-10                           0.110609   
2025-09-11                           0.099200   
2025-09-12                           0.105540   
2025-09-13                           0.102975   

            AVAX-USD_vol_adjusted_trend_signal  
date                                            
2025-09-09                            0.041567  
2025-09-10                            0.016734  
2025-09-11                            0.019340  
2025-09-12                            0.040714  
2025-09-13                            0.057396

In [404]:
cfg

{'portfolio': {'exchange': 'Coinbase Advanced', 'name': 'Trend Following'},
 'run': {'start_date': '2022-04-01',
  'end_date': '2025-07-31',
  'use_specific_start_date': True,
  'signal_start_date': '2022-04-01',
  'warmup_days': 300,
  'long_only': True,
  'annual_trading_days': 365,
  'initial_capital': 15000},
 'universe': {'tickers': ['BTC-USD',
   'ETH-USD',
   'SOL-USD',
   'ADA-USD',
   'AVAX-USD']},
 'data': {'use_coinbase_data': True,
  'use_saved_files': True,
  'saved_file_end_date': '2025-07-31',
  'price_or_returns_calc': 'price',
  'moving_avg_type': 'exponential'},
 'signals': {'moving_average': {'fast_mavg': 20,
   'slow_mavg': 200,
   'mavg_stepsize': 8,
   'mavg_z_score_window': 126},
  'donchian': {'entry_rolling_donchian_window': 56,
   'exit_rolling_donchian_window': 28,
   'use_donchian_exit_gate': False},
  'weighting': {'ma_crossover_signal_weight': 0.9,
   'donchian_signal_weight': 0.1,
   'weighted_signal_ewm_window': 4},
  'activation': {'use_activation': Fal

In [344]:
df_target_notional[vol_adj_signal_cols].iloc[-1].sum()

0.8663351283720252

In [346]:
1/df_target_notional[vol_adj_signal_cols].iloc[-1].sum()

1.1542877199025179

In [288]:
desired_positions

{'BTC-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0},
 'ETH-USD': {'new_trade_notional': 279.92314587564573,
  'trade_fees': 3.555023952620701},
 'SOL-USD': {'new_trade_notional': 272.80122292999977,
  'trade_fees': 3.464575531210997},
 'ADA-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0},
 'AVAX-USD': {'new_trade_notional': 0.0, 'trade_fees': 0.0}}

In [204]:
desired_positions

{'BTC-USD': {'new_trade_notional': 0, 'trade_fees': 0},
 'ETH-USD': {'new_trade_notional': 279.92314587564573,
  'trade_fees': 3.555023952620701},
 'SOL-USD': {'new_trade_notional': 272.80122292999977,
  'trade_fees': 3.464575531210997},
 'ADA-USD': {'new_trade_notional': 73.98175239403378,
  'trade_fees': 0.939568255404229},
 'AVAX-USD': {'new_trade_notional': 14.366597777876404,
  'trade_fees': 0.18245579177903032}}

In [162]:
desired_positions

{'BTC-USD': {'new_trade_notional': 0, 'trade_fees': 0},
 'ETH-USD': {'new_trade_notional': 283.5675160000648,
  'trade_fees': 3.601307453200823},
 'SOL-USD': {'new_trade_notional': 254.75915384755226,
  'trade_fees': 3.2354412538639137},
 'ADA-USD': {'new_trade_notional': 80.72584358149855,
  'trade_fees': 1.0252182134850316},
 'AVAX-USD': {'new_trade_notional': 12.412111052709395,
  'trade_fees': 0.15763381036940932}}

In [210]:
cash_shrink_factor

1.0

In [212]:
df_target_notional.tail()

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2025-09-07                      2834.664480                               0.0   
2025-09-08                      2698.028815                               0.0   
2025-09-09                      2664.010833                               0.0   
2025-09-10                      2650.985039                               0.0   
2025-09-11                      2726.372178                               0.0   

            BTC-USD_actual_position_size  BTC-USD_annualized_volatility_30  \
date                                                                         
2025-09-07                           0.0                          0.349947   
2025-09-08                           0.0                          0.351240   
2025-09-09                           0.0                          0.352946   
2025-09-10                           0.0                          0.341060   
2025-09-11                           0.0                          0.350855   

            BTC-USD_cash_shrink_factor  BTC-USD_close  \
date                                                    
2025-09-07                         0.0      111129.61   
2025-09-08                         0.0      112072.57   
2025-09-09                         0.0      111549.32   
2025-09-10                         0.0      113983.97   
2025-09-11                         0.0      114087.65   

            BTC-USD_cooldown_counter  BTC-USD_event  BTC-USD_final_signal  \
date                                                                        
2025-09-07                       0.0            NaN                   0.0   
2025-09-08                       0.0            NaN                   0.0   
2025-09-09                       0.0            NaN                   0.0   
2025-09-10                       0.0            NaN                   0.0   
2025-09-11                       0.0            NaN                   0.0   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2025-09-07                               -0.392511   
2025-09-08                               -0.410853   
2025-09-09                               -0.422202   
2025-09-10                               -0.434271   
2025-09-11                               -0.434296   

            BTC-USD_new_position_entry_exit_price  \
date                                                
2025-09-07                                    0.0   
2025-09-08                                    0.0   
2025-09-09                                    0.0   
2025-09-10                                    0.0   
2025-09-11                                    0.0   

            BTC-USD_new_position_notional  BTC-USD_new_position_size  \
date                                                                   
2025-09-07                            0.0                        0.0   
2025-09-08                            0.0                        0.0   
2025-09-09                            0.0                        0.0   
2025-09-10                            0.0                        0.0   
2025-09-11                            0.0                        0.0   

            BTC-USD_open  BTC-USD_open_position_notional  \
date                                                       
2025-09-07     110214.21                             0.0   
2025-09-08     111120.38                             0.0   
2025-09-09     112072.57                             0.0   
2025-09-10     111546.61                             0.0   
2025-09-11     113983.98                             0.0   

            BTC-USD_open_position_size  BTC-USD_short_sale_proceeds  \
date                                                                  
2025-09-07                         0.0                          0.0   
2025-09-08                         0.0                          0.0

In [152]:
(0.55 / np.sqrt(365)) / 0.034907

0.8247146916796562

In [154]:
signal_cols = [f'{ticker}_final_signal' for ticker in cfg['universe']['tickers']]
vol_adj_signal_cols = [f'{ticker}_vol_adjusted_trend_signal' for ticker in cfg['universe']['tickers']]
df_target_notional[signal_cols + vol_adj_signal_cols].tail()

BTC-USD_final_signal  ETH-USD_final_signal  SOL-USD_final_signal  \
date                                                                           
2025-09-06                   0.0              0.333888              0.217510   
2025-09-07                   0.0              0.330857              0.245517   
2025-09-08                   0.0              0.326951              0.267158   
2025-09-09                   0.0              0.322408              0.288805   
2025-09-10                   0.0              0.317475              0.308776   

            ADA-USD_final_signal  AVAX-USD_final_signal  \
date                                                      
2025-09-06              0.066246               0.014694   
2025-09-07              0.079435               0.032930   
2025-09-08              0.089375               0.046839   
2025-09-09              0.096375               0.036332   
2025-09-10              0.088936               0.014644   

            BTC-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-06                                0.0   
2025-09-07                                0.0   
2025-09-08                                0.0   
2025-09-09                                0.0   
2025-09-10                                0.0   

            ETH-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-06                           0.377855   
2025-09-07                           0.383974   
2025-09-08                           0.380945   
2025-09-09                           0.387930   
2025-09-10                           0.382044   

            SOL-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-06                           0.242912   
2025-09-07                           0.276073   
2025-09-08                           0.298942   
2025-09-09                           0.321004   
2025-09-10                           0.343231   

            ADA-USD_vol_adjusted_trend_signal  \
date                                            
2025-09-06                           0.079578   
2025-09-07                           0.098304   
2025-09-08                           0.110275   
2025-09-09                           0.117841   
2025-09-10                           0.108760   

            AVAX-USD_vol_adjusted_trend_signal  
date                                            
2025-09-06                            0.016498  
2025-09-07                            0.037649  
2025-09-08                            0.053606  
2025-09-09                            0.041521  
2025-09-10                            0.016723

In [140]:
actual_position_cols = [f'{ticker}_actual_position_notional' for ticker in cfg['universe']['tickers']]
df_target_notional[actual_position_cols].tail()

BTC-USD_actual_position_notional  \
date                                           
2025-09-06                               0.0   
2025-09-07                               0.0   
2025-09-08                               0.0   
2025-09-09                               0.0   
2025-09-10                               0.0   

            ETH-USD_actual_position_notional  \
date                                           
2025-09-06                               0.0   
2025-09-07                               0.0   
2025-09-08                               0.0   
2025-09-09                               0.0   
2025-09-10                               0.0   

            SOL-USD_actual_position_notional  \
date                                           
2025-09-06                               0.0   
2025-09-07                               0.0   
2025-09-08                               0.0   
2025-09-09                               0.0   
2025-09-10                               0.0   

            ADA-USD_actual_position_notional  \
date                                           
2025-09-06                               0.0   
2025-09-07                               0.0   
2025-09-08                               0.0   
2025-09-09                               0.0   
2025-09-10                               0.0   

            AVAX-USD_actual_position_notional  
date                                           
2025-09-06                                0.0  
2025-09-07                                0.0  
2025-09-08                                0.0  
2025-09-09                                0.0  
2025-09-10                                0.0

In [138]:
target_notional_cols = [f'{ticker}_target_notional' for ticker in cfg['universe']['tickers']]
df_target_notional[target_notional_cols].tail()

BTC-USD_target_notional  ETH-USD_target_notional  \
date                                                           
2025-09-06                      0.0                 0.000000   
2025-09-07                      0.0                 0.000000   
2025-09-08                      0.0                 0.000000   
2025-09-09                      0.0                 0.000000   
2025-09-10                      0.0               283.567516   

            SOL-USD_target_notional  ADA-USD_target_notional  \
date                                                           
2025-09-06                 0.000000                 0.000000   
2025-09-07                 0.000000                 0.000000   
2025-09-08                 0.000000                 0.000000   
2025-09-09                 0.000000                 0.000000   
2025-09-10               254.759154                80.725844   

            AVAX-USD_target_notional  
date                                  
2025-09-06                  0.000000  
2025-09-07                  0.000000  
2025-09-08                  0.000000  
2025-09-09                  0.000000  
2025-09-10                 12.412111

In [142]:
283.567516+254.759154+80.725844+12.412111

631.464625

In [21]:
print('Calculating Volatility Targeted Position Size and Cash Management!!')
## Get Target Volatility Position Sizing and Run Cash Management
target_vol_kwargs = {
    "df": df_signal,
    "ticker_list": cfg['universe']['tickers'],
    "initial_capital": cfg['run']['initial_capital'],
    "rolling_cov_window": cfg['risk_and_sizing']['rolling_cov_window'],
    "rolling_atr_window": cfg['risk_and_sizing']['rolling_atr_window'],
    "atr_multiplier": cfg['risk_and_sizing']['atr_multiplier'],
    "cash_buffer_percentage": cfg['risk_and_sizing']['cash_buffer_percentage'],
    "annualized_target_volatility": cfg['risk_and_sizing']['annualized_target_volatility'],
    "transaction_cost_est": cfg['execution_and_costs']['transaction_cost_est'],
    "passive_trade_rate": cfg['execution_and_costs']['passive_trade_rate'],
    "notional_threshold_pct": cfg['execution_and_costs']['notional_threshold_pct'],
    "min_trade_notional_abs": cfg['execution_and_costs']['min_trade_notional_abs'],
    "cooldown_counter_threshold": cfg['execution_and_costs']['cooldown_counter_threshold'],
    "annual_trading_days": cfg['run']['annual_trading_days'],
    "use_specific_start_date": False,
    "signal_start_date": cfg['run']['signal_start_date']
}

# df_final, desired_positions = get_target_notional_by_ticker(**target_vol_kwargs)
df_target_notional = get_target_notional_by_ticker(**target_vol_kwargs)

Calculating Volatility Targeted Position Size and Cash Management!!


In [22]:
df_target_notional

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2024-12-03                      3639.756531                               0.0   
2024-12-04                      3553.951147                               0.0   
2024-12-05                      3656.274847                               0.0   
2024-12-06                      4445.595338                               0.0   
2024-12-07                      4563.150068                               0.0   
2024-12-08                      4278.139585                               0.0   
2024-12-09                      4128.353910                               0.0   
2024-12-10                      4408.504014                               0.0   
2024-12-11                      4375.769346                               0.0   
2024-12-12                      4555.428456                               0.0   
2024-12-13                      4435.540984                               0.0   
2024-12-14                      4273.900890                               0.0   
2024-12-15                      4062.100806                               0.0   
2024-12-16                      4044.630253                               0.0   
2024-12-17                      4094.530229                               0.0   
2024-12-18                      3995.137826                               0.0   
2024-12-19                      4242.106604                               0.0   
2024-12-20                      4529.196452                               0.0   
2024-12-21                      4670.873932                               0.0   
2024-12-22                      4533.511653                               0.0   
2024-12-23                      4406.986734                               0.0   
2024-12-24                      4374.813711                               0.0   
2024-12-25                      4531.283834                               0.0   
2024-12-26                      4283.298707                               0.0   
2024-12-27                      4332.800735                               0.0   
2024-12-28                      4311.215903                               0.0   
2024-12-29                      4046.476293                               0.0   
2024-12-30                      3882.867122                               0.0   
2024-12-31                      3859.669301                               0.0   
2025-01-01                      3897.968415                               0.0   
2025-01-02                      3737.902852                               0.0   
2025-01-03                      3724.768295                               0.0   
2025-01-04                      3651.294171                               0.0   
2025-01-05                      3422.063298                               0.0   
2025-01-06                      3245.104889                               0.0   
2025-01-07                      3374.142518                               0.0   
2025-01-08                      3684.307993                               0.0   
2025-01-09                      3786.216755                               0.0   
2025-01-10                      3823.363731                               0.0   
2025-01-11                      3807.202423                               0.0   
2025-01-12                      3556.954573                               0.0   
2025-01-13                      3381.391281                               0.0   
2025-01-14                      3713.769254                               0.0   
2025-01-15                      3649.784563                               0.0   
2025-01-16                      3713.276510                               0.0   
2025-01-17                      3702.718747                               0.0   
2025-01-18                      3924.573152                               0.0   
2025-01-19                      3807.918566

In [23]:
df_target_notional.head()

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2024-12-03                      3639.756531                               0.0   
2024-12-04                      3553.951147                               0.0   
2024-12-05                      3656.274847                               0.0   
2024-12-06                      4445.595338                               0.0   
2024-12-07                      4563.150068                               0.0   

            BTC-USD_actual_position_size  BTC-USD_annualized_volatility_30  \
date                                                                         
2024-12-03                           0.0                               NaN   
2024-12-04                           0.0                               NaN   
2024-12-05                           0.0                               NaN   
2024-12-06                           0.0                               NaN   
2024-12-07                           0.0                               NaN   

            BTC-USD_cash_shrink_factor  BTC-USD_close  \
date                                                    
2024-12-03                         0.0       95924.52   
2024-12-04                         0.0       98746.24   
2024-12-05                         0.0       97044.23   
2024-12-06                         0.0       99891.35   
2024-12-07                         0.0       99929.32   

            BTC-USD_cooldown_counter  BTC-USD_event  BTC-USD_final_signal  \
date                                                                        
2024-12-03                       0.0            NaN                   NaN   
2024-12-04                       0.0            NaN                   NaN   
2024-12-05                       0.0            NaN                   NaN   
2024-12-06                       0.0            NaN                   NaN   
2024-12-07                       0.0            NaN                   NaN   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2024-12-03                                     NaN   
2024-12-04                                     NaN   
2024-12-05                                     NaN   
2024-12-06                                     NaN   
2024-12-07                                     NaN   

            BTC-USD_new_position_entry_exit_price  \
date                                                
2024-12-03                                    0.0   
2024-12-04                                    0.0   
2024-12-05                                    0.0   
2024-12-06                                    0.0   
2024-12-07                                    0.0   

            BTC-USD_new_position_notional  BTC-USD_new_position_size  \
date                                                                   
2024-12-03                            0.0                        0.0   
2024-12-04                            0.0                        0.0   
2024-12-05                            0.0                        0.0   
2024-12-06                            0.0                        0.0   
2024-12-07                            0.0                        0.0   

            BTC-USD_open  BTC-USD_open_position_notional  \
date                                                       
2024-12-03      95862.89                             0.0   
2024-12-04      95924.85                             0.0   
2024-12-05      98746.24                             0.0   
2024-12-06      97049.47                             0.0   
2024-12-07      99885.37                             0.0   

            BTC-USD_open_position_size  BTC-USD_short_sale_proceeds  \
date                                                                  
2024-12-03                         0.0                          0.0   
2024-12-04                         0.0                          0.0

In [72]:
desired_positions

{'BTC-USD': {'new_trade_notional': 0, 'trade_fees': 0},
 'ETH-USD': {'new_trade_notional': 5006.903890841127,
  'trade_fees': 63.58767941368231},
 'SOL-USD': {'new_trade_notional': 2692.3722783016624,
  'trade_fees': 34.19312793443111},
 'ADA-USD': {'new_trade_notional': 763.3374008212526,
  'trade_fees': 9.694384990429906},
 'AVAX-USD': {'new_trade_notional': 0, 'trade_fees': 0}}

In [48]:
cash_shrink_factor

1.0

In [62]:
## Calculate the covariance matrix for tickers in the portfolio
returns_cols = [f'{ticker}_t_1_close_pct_returns' for ticker in cfg['universe']['tickers']]
cov_matrix = df[returns_cols].rolling(cfg['risk_and_sizing']['rolling_cov_window']).cov(pairwise=True).dropna()

In [64]:
cov_matrix

BTC-USD_t_1_close_pct_returns  \
date                                                                       
2024-12-19 BTC-USD_t_1_close_pct_returns                        0.000588   
           ETH-USD_t_1_close_pct_returns                        0.000734   
           SOL-USD_t_1_close_pct_returns                        0.000594   
           ADA-USD_t_1_close_pct_returns                        0.000866   
           AVAX-USD_t_1_close_pct_returns                       0.000929   
2024-12-20 BTC-USD_t_1_close_pct_returns                        0.000616   
           ETH-USD_t_1_close_pct_returns                        0.000818   
           SOL-USD_t_1_close_pct_returns                        0.000645   
           ADA-USD_t_1_close_pct_returns                        0.000953   
           AVAX-USD_t_1_close_pct_returns                       0.001022   
2024-12-21 BTC-USD_t_1_close_pct_returns                        0.000610   
           ETH-USD_t_1_close_pct_returns                        0.000841   
           SOL-USD_t_1_close_pct_returns                        0.000639   
           ADA-USD_t_1_close_pct_returns                        0.000975   
           AVAX-USD_t_1_close_pct_returns                       0.001029   
2024-12-22 BTC-USD_t_1_close_pct_returns                        0.000609   
           ETH-USD_t_1_close_pct_returns                        0.000851   
           SOL-USD_t_1_close_pct_returns                        0.000654   
           ADA-USD_t_1_close_pct_returns                        0.000958   
           AVAX-USD_t_1_close_pct_returns                       0.001043   
2024-12-23 BTC-USD_t_1_close_pct_returns                        0.000624   
           ETH-USD_t_1_close_pct_returns                        0.000856   
           SOL-USD_t_1_close_pct_returns                        0.000620   
           ADA-USD_t_1_close_pct_returns                        0.001016   
           AVAX-USD_t_1_close_pct_returns                       0.001186   
2024-12-24 BTC-USD_t_1_close_pct_returns                        0.000624   
           ETH-USD_t_1_close_pct_returns                        0.000848   
           SOL-USD_t_1_close_pct_returns                        0.000608   
           ADA-USD_t_1_close_pct_returns                        0.001006   
           AVAX-USD_t_1_close_pct_returns                       0.001173   
2024-12-25 BTC-USD_t_1_close_pct_returns                        0.000664   
           ETH-USD_t_1_close_pct_returns                        0.000799   
           SOL-USD_t_1_close_pct_returns                        0.000722   
           ADA-USD_t_1_close_pct_returns                        0.001040   
           AVAX-USD_t_1_close_pct_returns                       0.001239   
2024-12-26 BTC-USD_t_1_close_pct_returns                        0.000650   
           ETH-USD_t_1_close_pct_returns                        0.000790   
           SOL-USD_t_1_close_pct_returns                        0.000760   
           ADA-USD_t_1_close_pct_returns                        0.001024   
           AVAX-USD_t_1_close_pct_returns                       0.001197   
2024-12-27 BTC-USD_t_1_close_pct_returns                        0.000675   
           ETH-USD_t_1_close_pct_returns                        0.000772   
           SOL-USD_t_1_close_pct_returns                        0.000809   
           ADA-USD_t_1_close_pct_returns                        0.001007   
           AVAX-USD_t_1_close_pct_returns                       0.001229   
2024-12-28 BTC-USD_t_1_close_pct_returns                        0.000684   
           ETH-USD_t_1_close_pct_returns                        0.000765   
           SOL-USD_t_1_close_pct_returns                        0.000815   
           ADA-USD_t_1_close_pct_returns                        0.000984   
           AVAX-USD_t_1_close_pct_returns                       0.001234   
2024-12-29 BTC-USD_t_1_close_pct_returns                        0.000681   
           ETH-

In [ ]:
price_map = get_price_map(cn_client, ticker_list=cfg['universe']['tickers'])
by_asset = {str(row["asset"]): row for _, row in df_portfolio_positions.iterrows()}
out = {}
for t in cfg['universe']['tickers']:
    base = t.split("-")[0]
    row = by_asset.get(base)
    qty = float(row["total_balance_crypto"]) if row is not None else 0.0
    px  = float(price_map[t])  # best bid/ask mid or last trade
    out[t] = {"qty": qty, "notional": qty * px, "price": px}

In [223]:
float(price_map['BTC-USD']['best_mid_price'])

111452.345

In [158]:
cn_client.get_best_bid_ask('BTC-USD')['pricebooks'][0]#['bids']

{'product_id': 'BTC-USD', 'bids': [{'price': '111322.51', 'size': '0.04499418'}], 'asks': [{'price': '111322.52', 'size': '1.22541447'}], 'time': '2025-09-09T01:38:45.923057Z'}

In [160]:
cn_client.get_product_book('BTC-USD', limit=1)['pricebook']['bids'][0]

{'price': '111322.51', 'size': '0.00006296'}

In [82]:
book = cn_client.get_product_book('BTC-USD', limit=1)['pricebook']

In [152]:
def get_price_map(client, ticker_list):
    result_dict = {}
    for ticker in ticker_list:
        ## Get Best Bid and Offer Data
        book = client.get_product_book(ticker, limit=1)['pricebook']
    
        ## Build Price Dictionary
        price_dict = {'best_bid_price': float(book['bids'][0]['price']),
                      'best_bid_size': float(book['bids'][0]['size']),
                      'best_ask_price': float(book['asks'][0]['price']),
                      'best_ask_size': float(book['asks'][0]['size']),
                      'best_mid_price': (float(book['bids'][0]['price']) + float(book['asks'][0]['price'])) / 2}
    
        result_dict[ticker] = price_dict

    return result_dict

In [142]:
book_test = cn_client.get_product_book('BTC-USD', limit=1)['pricebook']

In [144]:
book_test

{'product_id': 'BTC-USD', 'bids': [{'price': '111352.87', 'size': '0.00000134'}], 'asks': [{'price': '111352.88', 'size': '0.01689584'}], 'time': '2025-09-09T01:35:05.957196Z'}

In [146]:
getattr(book_test, 'bids', None)

[{'price': '111352.87', 'size': '0.00000134'}]

In [150]:
book_test['bids'][0]

{'price': '111352.87', 'size': '0.00000134'}

In [162]:
price_map = get_price_map(client=cn_client, ticker_list=cfg['universe']['tickers'])

In [163]:
price_map

{'BTC-USD': {'best_bid_price': 111322.51,
  'best_bid_size': 0.0449376,
  'best_ask_price': 111322.52,
  'best_ask_size': 1.48012882,
  'best_mid_price': 111322.515},
 'ETH-USD': {'best_bid_price': 4283.95,
  'best_bid_size': 0.25037545,
  'best_ask_price': 4283.99,
  'best_ask_size': 0.9897,
  'best_mid_price': 4283.969999999999},
 'SOL-USD': {'best_bid_price': 212.37,
  'best_bid_size': 0.01650666,
  'best_ask_price': 212.38,
  'best_ask_size': 19.45252482,
  'best_mid_price': 212.375},
 'ADA-USD': {'best_bid_price': 0.8645,
  'best_bid_size': 1661.36444109,
  'best_ask_price': 0.8646,
  'best_ask_size': 9586.58556201,
  'best_mid_price': 0.86455},
 'AVAX-USD': {'best_bid_price': 25.12,
  'best_bid_size': 22.02731496,
  'best_ask_price': 25.13,
  'best_ask_size': 453.03381537,
  'best_mid_price': 25.125}}

In [112]:
result_dict

{'BTC-USD': {'best_bid_price': 111878.2,
  'best_bid_size': 0.02524951,
  'best_ask_price': 111878.21,
  'best_ask_size': 111878.21,
  'best_mid_price': 111878.2},
 'ETH-USD': {'best_bid_price': 4321.16,
  'best_bid_size': 0.62907113,
  'best_ask_price': 4321.17,
  'best_ask_size': 4321.17,
  'best_mid_price': 4321.16},
 'SOL-USD': {'best_bid_price': 213.56,
  'best_bid_size': 1.61711148,
  'best_ask_price': 213.57,
  'best_ask_size': 213.57,
  'best_mid_price': 213.56},
 'ADA-USD': {'best_bid_price': 0.8503,
  'best_bid_size': 5.80907553,
  'best_ask_price': 0.8504,
  'best_ask_size': 0.8504,
  'best_mid_price': 0.8503},
 'AVAX-USD': {'best_bid_price': 25.16,
  'best_bid_size': 779.89532244,
  'best_ask_price': 25.17,
  'best_ask_size': 25.17,
  'best_mid_price': 25.16}}

In [106]:
price_dict

{'best_bid_price': 111940.4,
 'best_bid_size': 0.03422194,
 'best_ask_price': 111940.41,
 'best_ask_size': 111940.41,
 'best_mid_price': 111940.4}

In [98]:
float(book['bids'][0]['price'])

111940.4

In [ ]:
cn_client.get_product

In [108]:
by_asset['AMP']

asset                                                            AMP
account_uuid                    0c34eeaf-64e5-5b2a-99a3-326747eefdda
asset_uuid                      f3b62870-ddd0-5dea-9d80-5190d8558461
total_balance_fiat                                         16.724867
available_to_trade_fiat                                    16.724867
total_balance_crypto                                       5060.4746
allocation                                                  0.000674
cost_basis_value                        252.980000000000025777993951
cost_basis_currency                                              USD
is_cash                                                        False
average_entry_price_value                         0.0499913607169585
average_entry_price_currency                                     USD
available_to_trade_crypto                                  5060.4746
unrealized_pnl                                            -236.25513
available_to_transfer_fiat        

In [56]:
## Get Portfolio UUID
cn_client = cn.get_coinbase_rest_api_client(cn.key_location)
portfolio_uuid = cn.get_portfolio_uuid(cn_client, portfolio_name='Default')

df_portfolio_positions = cn.get_portfolio_breakdown(cn_client, portfolio_uuid)

In [64]:
float(df_portfolio_positions['total_balance_fiat'].sum())

24810.334453862004

In [102]:
portfolio_list = cn_client.get_portfolios()['portfolios']
portfolio_name = 'Default'
if portfolio_name == 'Trend Following':
    portfolio = next((p for p in portfolio_list
                      if p['name'] == 'Trend Following' and not p['deleted']), None)
else:
    portfolio = next((p for p in portfolio_list
                      if p['name'] == 'Default' and not p['deleted']), None)

In [104]:
portfolio

{'name': 'Default', 'uuid': '745aae95-4dd9-5888-ab3d-39d549d91a29', 'type': 'DEFAULT', 'deleted': False}

In [96]:
portfolios[0]['deleted']

False

In [38]:
cn_client = cn.get_coinbase_rest_api_client(cn.key_location)
df_portfolio_positions = cn.get_portfolio_breakdown(cn_client)

In [70]:
cn_client.get_portfolios()['portfolios']

[{'name': 'Default', 'uuid': '745aae95-4dd9-5888-ab3d-39d549d91a29', 'type': 'DEFAULT', 'deleted': False},
 {'name': 'Trend Following', 'uuid': '4cceea8c-1577-493c-a238-1443e9f31a0d', 'type': 'CONSUMER', 'deleted': False}]

In [39]:
[f'{i[:-4]}' for i in cfg['universe']['tickers']]

['BTC', 'ETH', 'SOL', 'ADA', 'AVAX']

In [68]:
df_portfolio_positions[df_portfolio_positions.is_cash]#[df_portfolio_positions.asset.isin([f'{i[:-4]}' for i in cfg['universe']['tickers']])]#.head()

asset                          account_uuid asset_uuid  total_balance_fiat  \
10   USD  5d758151-9bd0-50f2-bda2-a8e9973cc40c                      45.306778   

    available_to_trade_fiat  total_balance_crypto  allocation  \
10                45.306778             45.306778    0.001826   

   cost_basis_value cost_basis_currency  is_cash average_entry_price_value  \
10  45.306779523968                 USD     True                         1   

   average_entry_price_currency  available_to_trade_crypto  unrealized_pnl  \
10                          USD                  45.306778             0.0   

    available_to_transfer_fiat  available_to_transfer_crpyto  
10                   45.306778                     45.306778

In [46]:
df_portfolio_positions[df_portfolio_positions.is_cash == True]

asset                          account_uuid asset_uuid  total_balance_fiat  \
10   USD  5d758151-9bd0-50f2-bda2-a8e9973cc40c                      45.306778   

    available_to_trade_fiat  total_balance_crypto  allocation  \
10                45.306778             45.306778     0.00183   

   cost_basis_value cost_basis_currency  is_cash average_entry_price_value  \
10  45.306779523968                 USD     True                         1   

   average_entry_price_currency  available_to_trade_crypto  unrealized_pnl  \
10                          USD                  45.306778             0.0   

    available_to_transfer_fiat  available_to_transfer_crpyto  
10                   45.306778                     45.306778

In [17]:
print('Calculating Volatility Targeted Position Size and Cash Management!!')
## Get Target Volatility Position Sizing and Run Cash Management
target_vol_kwargs = {
    "df": df_signal,
    "ticker_list": cfg['universe']['tickers'],
    "initial_capital": cfg['run']['initial_capital'],
    "rolling_cov_window": cfg['risk_and_sizing']['rolling_cov_window'],
    "rolling_atr_window": cfg['risk_and_sizing']['rolling_atr_window'],
    "atr_multiplier": cfg['risk_and_sizing']['atr_multiplier'],
    "cash_buffer_percentage": cfg['risk_and_sizing']['cash_buffer_percentage'],
    "annualized_target_volatility": cfg['risk_and_sizing']['annualized_target_volatility'],
    "transaction_cost_est": cfg['execution_and_costs']['transaction_cost_est'],
    "passive_trade_rate": cfg['execution_and_costs']['passive_trade_rate'],
    "notional_threshold_pct": cfg['execution_and_costs']['notional_threshold_pct'],
    "min_trade_notional_abs": cfg['execution_and_costs']['min_trade_notional_abs'],
    "cooldown_counter_threshold": cfg['execution_and_costs']['cooldown_counter_threshold'],
    "annual_trading_days": cfg['run']['annual_trading_days'],
    "use_specific_start_date": False,
    "signal_start_date": cfg['run']['signal_start_date']
}
df = size_cont.get_target_volatility_daily_portfolio_positions(**target_vol_kwargs)
# df = size_cont.get_target_volatility_daily_portfolio_positions(
#     df_signal, ticker_list=cfg['universe']['tickers'], initial_capital=cfg['run']['initial_capital'], rolling_cov_window=cfg['risk_and_sizing']['rolling_cov_window'],
#     rolling_atr_window=cfg['risk_and_sizing']['rolling_atr_window'], atr_multiplier=cfg['risk_and_sizing']['atr_multiplier'],
#     cash_buffer_percentage=cfg['risk_and_sizing']['cash_buffer_percentage'], annualized_target_volatility=cfg['risk_and_sizing']['annualized_target_volatility'],
#     transaction_cost_est=cfg['execution_and_costs']['transaction_cost_est'], passive_trade_rate=cfg['execution_and_costs']['passive_trade_rate'],
#     notional_threshold_pct=cfg['execution_and_costs']['notional_threshold_pct'], cooldown_counter_threshold=cfg['execution_and_costs']['cooldown_counter_threshold'],
#     annual_trading_days=cfg['run']['annual_trading_days'], use_specific_start_date=False,
#     signal_start_date=start_date)

Calculating Volatility Targeted Position Size and Cash Management!!


In [ ]:
df_signal.tail()

In [20]:
df.tail()

BTC-USD_20_avg_true_range_price  BTC-USD_actual_position_notional  \
date                                                                            
2025-09-01                      3081.499094                               0.0   
2025-09-02                      3041.119180                               0.0   
2025-09-03                      3075.475448                               0.0   
2025-09-04                      2979.356834                               0.0   
2025-09-05                      2973.189517                               0.0   

            BTC-USD_actual_position_size  BTC-USD_annualized_volatility_30  \
date                                                                         
2025-09-01                           0.0                          0.357586   
2025-09-02                           0.0                          0.358963   
2025-09-03                           0.0                          0.361097   
2025-09-04                           0.0                          0.360454   
2025-09-05                           0.0                          0.360759   

            BTC-USD_cash_shrink_factor  BTC-USD_close  \
date                                                    
2025-09-01                         0.0      109240.55   
2025-09-02                         0.0      111247.94   
2025-09-03                         0.0      111756.41   
2025-09-04                         0.0      110720.79   
2025-09-05                         0.0      113131.95   

            BTC-USD_cooldown_counter BTC-USD_event  BTC-USD_final_signal  \
date                                                                       
2025-09-01                       0.0   No Position                   0.0   
2025-09-02                       0.0   No Position                   0.0   
2025-09-03                       0.0   No Position                   0.0   
2025-09-04                       0.0   No Position                   0.0   
2025-09-05                       0.0   No Position                   0.0   

            BTC-USD_final_weighted_additive_signal  \
date                                                 
2025-09-01                               -0.278088   
2025-09-02                               -0.322044   
2025-09-03                               -0.354528   
2025-09-04                               -0.379050   
2025-09-05                               -0.403311   

            BTC-USD_new_position_entry_exit_price  \
date                                                
2025-09-01                              108247.95   
2025-09-02                              109240.55   
2025-09-03                              111247.94   
2025-09-04                              111756.40   
2025-09-05                              110714.48   

            BTC-USD_new_position_notional  BTC-USD_new_position_size  \
date                                                                   
2025-09-01                            0.0                        0.0   
2025-09-02                            0.0                        0.0   
2025-09-03                            0.0                        0.0   
2025-09-04                            0.0                        0.0   
2025-09-05                            0.0                        0.0   

            BTC-USD_open  BTC-USD_open_position_notional  \
date                                                       
2025-09-01     108247.95                             0.0   
2025-09-02     109240.55                             0.0   
2025-09-03     111247.94                             0.0   
2025-09-04     111756.40                             0.0   
2025-09-05     110714.48                             0.0   

            BTC-USD_open_position_size  BTC-USD_short_sale_proceeds  \
date                                                                  
2025-09-01                         0.0                          0.0   
2025-09-02                         0.0                          0.0   
202

In [ ]:
df.tail()

In [ ]:
df['AVAX-USD_event']

In [24]:
df[target_notional_cols]

BTC-USD_target_notional  ETH-USD_target_notional  \
date                                                           
2024-11-30                 0.000000             0.000000e+00   
2024-12-01                 0.000000             0.000000e+00   
2024-12-02                 0.000000             0.000000e+00   
2024-12-03                 0.000000             0.000000e+00   
2024-12-04                 0.000000             0.000000e+00   
2024-12-05                 0.000000             0.000000e+00   
2024-12-06                 0.000000             0.000000e+00   
2024-12-07                 0.000000             0.000000e+00   
2024-12-08                 0.000000             0.000000e+00   
2024-12-09                 0.000000             0.000000e+00   
2024-12-10                 0.000000             0.000000e+00   
2024-12-11                 0.000000             0.000000e+00   
2024-12-12                 0.000000             0.000000e+00   
2024-12-13                 0.000000             0.000000e+00   
2024-12-14                 0.000000             0.000000e+00   
2024-12-15                 0.000000             0.000000e+00   
2024-12-16                 0.000000             0.000000e+00   
2024-12-17                 0.000000             0.000000e+00   
2024-12-18                 0.000000             0.000000e+00   
2024-12-19                 0.000000             0.000000e+00   
2024-12-20                 0.000000             0.000000e+00   
2024-12-21                 0.000000             0.000000e+00   
2024-12-22                 0.000000             0.000000e+00   
2024-12-23                 0.000000             0.000000e+00   
2024-12-24                 0.000000             0.000000e+00   
2024-12-25                 0.000000             0.000000e+00   
2024-12-26                 0.000000             0.000000e+00   
2024-12-27                 0.000000             0.000000e+00   
2024-12-28                 0.000000             0.000000e+00   
2024-12-29                 0.000000             0.000000e+00   
2024-12-30                 0.000000             0.000000e+00   
2024-12-31                 0.000000             0.000000e+00   
2025-01-01                 0.000000             0.000000e+00   
2025-01-02                 0.000000             0.000000e+00   
2025-01-03                 0.000000             0.000000e+00   
2025-01-04                 0.000000             0.000000e+00   
2025-01-05                 0.000000             0.000000e+00   
2025-01-06                 0.000000             0.000000e+00   
2025-01-07                 0.000000             0.000000e+00   
2025-01-08                 0.000000             0.000000e+00   
2025-01-09                 0.000000             0.000000e+00   
2025-01-10                 0.000000             0.000000e+00   
2025-01-11                 0.000000             0.000000e+00   
2025-01-12                 0.000000             0.000000e+00   
2025-01-13                 0.000000             0.000000e+00   
2025-01-14                 0.000000             0.000000e+00   
2025-01-15                 0.000000             0.000000e+00   
2025-01-16                 0.000000             0.000000e+00   
2025-01-17                 0.000000             0.000000e+00   
2025-01-18                 0.000000             0.000000e+00   
2025-01-19                 0.000000             0.000000e+00   
2025-01-20                 0.000000             0.000000e+00   
2025-01-21                 0.000000             0.000000e+00   
2025-01-22                 0.000000             0.000000e+00   
2025-01-23                 0.000000             0.000000e+00   
2025-01-24                 0.000000             0.000000e+00   
2025-01-25                 0.000000             0.000000e+00   
2025-01-26                 0.000000             0.000000e+00   
2025-01-27                 0.000000             0.000000e+00   
2025-01-28                 0.000000             0.000000e+00   
2025-01-29                 0.000000         

In [ ]:
df.iloc[-1]

In [ ]:
cfg

In [22]:
signal_cols = [f'{ticker}_final_signal' for ticker in cfg["universe"]["tickers"]]
vol_adj_signal_cols = [f'{ticker}_vol_adjusted_trend_signal' for ticker in cfg["universe"]["tickers"]]
target_notional_cols = [f'{ticker}_target_notional' for ticker in cfg["universe"]["tickers"]]
df_trend[signal_cols]

BTC-USD_final_signal  ETH-USD_final_signal  SOL-USD_final_signal  \
date                                                                           
2024-11-09                   NaN                   NaN                   NaN   
2024-11-10                   NaN                   NaN                   NaN   
2024-11-11                   NaN                   NaN                   NaN   
2024-11-12                   NaN                   NaN                   NaN   
2024-11-13                   NaN                   NaN                   NaN   
2024-11-14                   NaN                   NaN                   NaN   
2024-11-15                   NaN                   NaN                   NaN   
2024-11-16                   NaN                   NaN                   NaN   
2024-11-17                   NaN                   NaN                   NaN   
2024-11-18                   NaN                   NaN                   NaN   
2024-11-19                   NaN                   NaN                   NaN   
2024-11-20                   NaN                   NaN                   NaN   
2024-11-21                   NaN                   NaN                   NaN   
2024-11-22                   NaN                   NaN                   NaN   
2024-11-23                   NaN                   NaN                   NaN   
2024-11-24                   NaN                   NaN                   NaN   
2024-11-25                   NaN                   NaN                   NaN   
2024-11-26                   NaN                   NaN                   NaN   
2024-11-27                   NaN                   NaN                   NaN   
2024-11-28                   NaN                   NaN                   NaN   
2024-11-29                   NaN                   NaN                   NaN   
2024-11-30                   NaN                   NaN                   NaN   
2024-12-01                   NaN                   NaN                   NaN   
2024-12-02                   NaN                   NaN                   NaN   
2024-12-03                   NaN                   NaN                   NaN   
2024-12-04                   NaN                   NaN                   NaN   
2024-12-05                   NaN                   NaN                   NaN   
2024-12-06                   NaN                   NaN                   NaN   
2024-12-07                   NaN                   NaN                   NaN   
2024-12-08                   NaN                   NaN                   NaN   
2024-12-09                   NaN                   NaN                   NaN   
2024-12-10                   NaN                   NaN                   NaN   
2024-12-11                   NaN                   NaN                   NaN   
2024-12-12                   NaN                   NaN                   NaN   
2024-12-13                   NaN                   NaN                   NaN   
2024-12-14                   NaN                   NaN                   NaN   
2024-12-15                   NaN                   NaN                   NaN   
2024-12-16                   NaN                   NaN                   NaN   
2024-12-17                   NaN                   NaN                   NaN   
2024-12-18                   NaN                   NaN                   NaN   
2024-12-19                   NaN                   NaN                   NaN   
2024-12-20                   NaN                   NaN                   NaN   
2024-12-21                   NaN                   NaN                   NaN   
2024-12-22                   NaN                   NaN                   NaN   
2024-12-23                   NaN                   NaN                   NaN   
2024-12-24                   NaN                   NaN                   NaN   
2024-12-25                   NaN                   NaN                   NaN   
2024-12-26                   NaN                   NaN                   NaN   
2024-12-27  

In [ ]:
df_trend[vol_adj_signal_cols]

In [ ]:
def apply_target_volatility_position_sizing_continuous_strategy_with_rolling_r_sqr_vol_of_vol(
        start_date, end_date, ticker_list, fast_mavg, slow_mavg, mavg_stepsize, mavg_z_score_window,
        entry_rolling_donchian_window, exit_rolling_donchian_window, use_donchian_exit_gate,
        ma_crossover_signal_weight, donchian_signal_weight, weighted_signal_ewm_window,
        rolling_r2_window=30, lower_r_sqr_limit=0.2, upper_r_sqr_limit=0.8, r2_smooth_window=3, r2_confirm_days=0,
        log_std_window=14, coef_of_variation_window=30, vol_of_vol_z_score_window=252, vol_of_vol_p_min=0.6,
        r2_strong_threshold=0.8, use_activation=True, tanh_activation_constant_dict=None, moving_avg_type='exponential',
        long_only=False, price_or_returns_calc='price', initial_capital=15000, rolling_cov_window=20,
        volatility_window=20, rolling_atr_window=20, atr_multiplier=0.5, transaction_cost_est=0.001,
        passive_trade_rate=0.05, notional_threshold_pct=0.05, cooldown_counter_threshold=3, use_coinbase_data=True,
        use_saved_files=True, saved_file_end_date='2025-07-31', rolling_sharpe_window=50, cash_buffer_percentage=0.10,
        annualized_target_volatility=0.20, annual_trading_days=365, use_specific_start_date=False,
        signal_start_date=None):

    ## Check if data is available for all the tickers
    date_list = cn.coinbase_start_date_by_ticker_dict
    ticker_list = [ticker for ticker in ticker_list if pd.Timestamp(date_list[ticker]).date() < end_date]

    print('Generating Moving Average Ribbon Signal!!')
    ## Generate Trend Signal for all tickers

    df_trend = get_trend_donchian_signal_for_portfolio_with_rolling_r_sqr_vol_of_vol(
        start_date=start_date, end_date=end_date, ticker_list=ticker_list, fast_mavg=fast_mavg, slow_mavg=slow_mavg,
        mavg_stepsize=mavg_stepsize, mavg_z_score_window=mavg_z_score_window,
        entry_rolling_donchian_window=entry_rolling_donchian_window,
        exit_rolling_donchian_window=exit_rolling_donchian_window, use_donchian_exit_gate=use_donchian_exit_gate,
        ma_crossover_signal_weight=ma_crossover_signal_weight, donchian_signal_weight=donchian_signal_weight,
        weighted_signal_ewm_window=weighted_signal_ewm_window, rolling_r2_window=rolling_r2_window,
        lower_r_sqr_limit=lower_r_sqr_limit, upper_r_sqr_limit=upper_r_sqr_limit, r2_smooth_window=r2_smooth_window,
        r2_confirm_days=r2_confirm_days, log_std_window=log_std_window, coef_of_variation_window=coef_of_variation_window,
        vol_of_vol_z_score_window=vol_of_vol_z_score_window, vol_of_vol_p_min=vol_of_vol_p_min,
        r2_strong_threshold=r2_strong_threshold, use_activation=use_activation,
        tanh_activation_constant_dict=tanh_activation_constant_dict, moving_avg_type=moving_avg_type,
        long_only=long_only, price_or_returns_calc=price_or_returns_calc, use_coinbase_data=use_coinbase_data,
        use_saved_files=use_saved_files, saved_file_end_date=saved_file_end_date)

    print('Generating Volatility Adjusted Trend Signal!!')
    ## Get Volatility Adjusted Trend Signal
    df_signal = size_cont.get_volatility_adjusted_trend_signal_continuous(df_trend, ticker_list, volatility_window,
                                                                          annual_trading_days)

    print('Getting Average True Range for Stop Loss Calculation!!')
    ## Get Average True Range for Stop Loss Calculation
    df_atr = size_cont.get_average_true_range_portfolio(start_date=start_date, end_date=end_date,
                                                        ticker_list=ticker_list, rolling_atr_window=rolling_atr_window,
                                                        price_or_returns_calc='price',
                                                        use_coinbase_data=use_coinbase_data,
                                                        use_saved_files=use_saved_files,
                                                        saved_file_end_date=saved_file_end_date)
    df_signal = pd.merge(df_signal, df_atr, left_index=True, right_index=True, how='left')

    print('Calculating Volatility Targeted Position Size and Cash Management!!')
    ## Get Target Volatility Position Sizing and Run Cash Management
    df = size_cont.get_target_volatility_daily_portfolio_positions(
        df_signal, ticker_list=ticker_list, initial_capital=initial_capital, rolling_cov_window=rolling_cov_window,
        rolling_atr_window=rolling_atr_window, atr_multiplier=atr_multiplier,
        cash_buffer_percentage=cash_buffer_percentage, annualized_target_volatility=annualized_target_volatility,
        transaction_cost_est=transaction_cost_est, passive_trade_rate=passive_trade_rate,
        notional_threshold_pct=notional_threshold_pct, cooldown_counter_threshold=cooldown_counter_threshold,
        annual_trading_days=annual_trading_days, use_specific_start_date=use_specific_start_date,
        signal_start_date=signal_start_date)

    print('Calculating Portfolio Performance!!')
    ## Calculate Portfolio Performance
    df = size_bin.calculate_portfolio_returns(df, rolling_sharpe_window)

    return df
